# ML Denemeleri ve Gerekli Kütüphaneler

In [ ]:
#Gerekli Tüm kütüphaneler
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import yfinance as yf
import requests
from datetime import datetime, timedelta
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.linear_model import LinearRegression, Lasso, Ridge
from sklearn.svm import SVR
import xgboost as xgb
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error, mean_absolute_percentage_error
from statsmodels.stats.outliers_influence import variance_inflation_factor
from statsmodels.tools.tools import add_constant
from sklearn.decomposition import PCA

## `prepare_time_series_data_inf()`

+ Bazı şirketlerin, bazı satırlarındaki değerler `inf` oluyordu ve bu sorunu; lineer interpole kullanarak, o satırın bir önceki ve bir sonraki satırlarında bulunan değerlerin ortalamasını alarak doldurdum. `_inf` kısmı, bu sorunun çözümünü ifade ediyor.

In [ ]:
def prepare_time_series_data_inf(ticker, start_date="7y"):
    stock = yf.Ticker(ticker)
    df = stock.history(period=start_date)
    if df.empty:
        raise ValueError(f"{ticker} için veri alınamadı. Lütfen geçerli bir hisse sembolü girin.")

    df = df.reset_index()
    df["Date"] = pd.to_datetime(df["Date"]).dt.date
    df['Date'] = pd.to_datetime(df['Date'], errors='coerce')
    df['Close'] = pd.to_numeric(df['Close'], errors='coerce')

    # Feature Engineering
    df["Percentage_Change"] = ((df['Close'] - df['Open']) / df['Open']) * 100
    df['Volume_Percentage_Change'] = df['Volume'].pct_change() * 100
    df.dropna(inplace=True)

    df['MA_5'] = df['Close'].rolling(window=5).mean()
    df['MA_21'] = df['Close'].rolling(window=21).mean()
    df['MA_63'] = df['Close'].rolling(window=63).mean()
    df['MA_126'] = df['Close'].rolling(window=126).mean()
    df['MA_252'] = df['Close'].rolling(window=252).mean()

    df['EWMA_5'] = df['Close'].ewm(span=5, adjust=False).mean()
    df['EWMA_21'] = df['Close'].ewm(span=21, adjust=False).mean()
    df['EWMA_63'] = df['Close'].ewm(span=63, adjust=False).mean()
    df['EWMA_126'] = df['Close'].ewm(span=126, adjust=False).mean()
    df['EWMA_252'] = df['Close'].ewm(span=252, adjust=False).mean()

    # Sonsuz (inf) değerleri kontrol et ve NaN'a çevir
    df.replace([np.inf, -np.inf], np.nan, inplace=True)

    # NaN değerleri önceki ve sonraki değerlerin ortalamasıyla doldur
    df = df.interpolate(method='linear', limit_direction='both')

    df = df.drop(columns=["Open", "High", "Low", "Volume", "Dividends", "Stock Splits"], axis=1)
    df.dropna(inplace=True)
    df = df.reset_index(drop=True)
    return df

## `get_sp500_tickers`

In [ ]:
#Wikipedia'dan veri çekimi
import requests
import pandas as pd

def get_sp500_tickers():
    """
    S&P 500 şirketlerinin kodlarını Wikipedia'dan çeker.

    Returns:
        list: S&P 500 şirketlerinin kodlarının listesi.
    """
    url = "https://en.wikipedia.org/wiki/List_of_S%26P_500_companies"

    try:
        #Wikipedia'dan sayfa içeriğini çekme
        response = requests.get(url)
        response.raise_for_status()

        #Pandas ile HTML tablosunu okuma
        tables = pd.read_html(response.text)

        #İlk tablo S&P 500 şirketlerini içeriyor
        sp500_table = tables[0]

        #'Symbol' sütunundaki şirket kodlarını alma
        tickers = sp500_table['Symbol'].tolist()
        return tickers

    except Exception as e:
        print(f"Hata oluştu: {e}")
        return []

In [ ]:
tickers_inf = get_sp500_tickers()

<ipython-input-45-dba9470b9b90>:20: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  tables = pd.read_html(response.text)


In [ ]:
tickers_inf.remove("BRK.B")
tickers_inf.append("BRK-B")

In [ ]:
tickers_inf.remove("BF.B")
tickers_inf.append("BF-B")

## `dataframes_inf` dict

+ `dataframes_inf`, inf sorununa sahip olmayan şirketlerin kodları ve `prepare_time_series_data_inf()` fonksiyonu ile çekilen verilerinin mevcut olduğu sözlük. Bunu çalıştırmak yerine **29.01.2025** tarihinde çekilmiş verileri **.pkl** dosyası olarak indirdim. O dosya dict olarak import edilebilir.

In [ ]:
# Sözlükte verileri saklamak için bir boş sözlük oluşturuyoruz
dataframes_inf = {}

# Döngüyle her şirketin verisini çekiyoruz
for ticker in tickers_inf:
    try:
        print(f"{ticker} verileri çekiliyor...")
        dataframes_inf[ticker] = prepare_time_series_data_inf(ticker)
        print(f"{ticker} verileri başarıyla çekildi.")
    except Exception as e:
        print(f"{ticker} verileri alınamadı: {e}")

In [ ]:
import pickle
with open('dataframes_inf.pkl', 'rb') as f:
    dataframes_inf = pickle.load(f)

Error loading with default encoding. Trying with 'latin1' encoding...


UnpicklingError: invalid load key, '@'.

## `evaluate_models_inf_4` (ML Modelleri)

+ `inf` sorununu çözdükten sonra oluşturduğum, her şirket için 12'şer adet ML modeli eğiten ve tüm metrik sonuçlarını bir dataframe'e saklayan model eğitim fonksiyonu

In [ ]:
# Regressor modellerin tanımı
regression_models = {
    "DecisionTree": DecisionTreeRegressor(),
    "RandomForest": RandomForestRegressor(),
    "GradientBoosting": GradientBoostingRegressor(),
    "AdaBoost": AdaBoostRegressor(),
    "KNN": KNeighborsRegressor(),
    "LinearRegression": LinearRegression(),
    "LassoRegression": Lasso(),
    "RidgeRegression": Ridge(),
    "LinearSVR": SVR(kernel="linear"),
    "RbfSVR": SVR(kernel="rbf"),
    "PolynomialSVR": SVR(kernel="poly"),
    "XGBoost": xgb.XGBRegressor()
}

In [ ]:
#Sonuçları saklamak için global bir DataFrame oluştur
model_results = pd.DataFrame(columns=["Ticker", "Model", "Train_Accuracy", "Test_Accuracy", "MSE", "MAE", "R2"])

def evaluate_models_inf_4(stock_names=list()):
    global model_results  # Sonuçları burada biriktireceğiz

    # Beklenen sütunların listesi
    required_columns = [
        "Date", "Close", "Percentage_Change", "Volume_Percentage_Change",
        "MA_5", "MA_21", "MA_63", "MA_126", "MA_252",
        "EWMA_5", "EWMA_21", "EWMA_63", "EWMA_126", "EWMA_252"
    ]

    failed_tickers = []  # Model eğitilemeyen şirketleri kaydetmek için liste

    for ticker in stock_names:
        if ticker in dataframes_inf:
            print(f"\n=== {ticker} için Model Performansı Sonuçları ===")

            df = dataframes_inf[ticker]

            # Veri çerçevesi boş mu kontrol et
            if df.empty:
                print(f"{ticker} için veri çerçevesi boş, atlanıyor.")
                failed_tickers.append((ticker, "Empty dataframe"))
                continue

            # Eksik sütunları kontrol et
            missing_columns = [col for col in required_columns if col not in df.columns]
            if missing_columns:
                print(f"{ticker} için eksik sütunlar: {missing_columns}, atlanıyor.")
                failed_tickers.append((ticker, f"Missing columns: {missing_columns}"))
                continue

            try:
                # X ve y ayrımı
                X = df.drop(columns=["Date", "Close"], axis=1)
                y = df["Close"]

                # Standartlaştırma
                X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=False)
                scaler = StandardScaler()
                X_train_scaled = scaler.fit_transform(X_train)
                X_test_scaled = scaler.transform(X_test)

                # PCA Uygulanması
                pca = PCA(n_components=0.95)  # Varyansın %95'ini açıklayan bileşenler seçiliyor
                X_train_pca = pca.fit_transform(X_train_scaled)
                X_test_pca = pca.transform(X_test_scaled)

                for name, reg in regression_models.items():
                    try:
                        reg.fit(X_train_pca, y_train)
                        predictions = reg.predict(X_test_pca)
                        train_score = reg.score(X_train_pca, y_train)
                        test_score = reg.score(X_test_pca, y_test)
                        mse = mean_squared_error(y_test, predictions)
                        mae = mean_absolute_error(y_test, predictions)
                        mape = mean_absolute_percentage_error(y_test, predictions)
                        r2 = r2_score(y_test, predictions)

                        # Sonuçları model_results veri çerçevesine ekle
                        new_row = pd.DataFrame({
                            "Ticker": [ticker],
                            "Model": [name],
                            "Train_Accuracy": [train_score],
                            "Test_Accuracy": [test_score],
                            "MSE": [mse],
                            "MAE": [mae],
                            "MAPE": [mape],
                            "R2": [r2]
                        })

                        # pd.concat kullanımı
                        model_results = pd.concat([model_results, new_row], ignore_index=True)

                        print(f"\nModel: {name}")
                        print(f"Train Setindeki Doğruluk: {train_score}")
                        print(f"Test Setindeki Doğruluk: {test_score}")
                        print(f"MSE Skoru: {mse}")
                        print(f"MAE Skoru: {mae}")
                        print(f"MAPE Skoru: {mape}")
                        print(f"R^2 Skoru: {r2}")

                    except Exception as e:
                        print(f"{name} modeli {ticker} için hata verdi: {e}")

            except Exception as e:
                print(f"{ticker} için bir hata oluştu: {e}")
                failed_tickers.append((ticker, f"Model training error: {str(e)}"))
        else:
            print(f"\nTicker {ticker} not found in dataframes_inf, skipping...")  # Ticker bulunamazsa mesaj yazdır
            failed_tickers.append((ticker, "Ticker not found in dataframes_inf"))

    # Model eğitilemeyen şirketleri raporla
    if failed_tickers:
        print(f"\n=== Model Eğitilemeyen Şirketler ({len(failed_tickers)}) ===")
        for ticker, reason in failed_tickers:
            print(f"{ticker}: {reason}")


# Daha Fazla FeatureEngineering ile `prepare_time_series_data_inf()` Fonksiyonunun Geliştirilmesi (`prepare_time_series_data_dev`)

**Yapılan Değişiklikler ve Eklemeler:**

+

In [ ]:
#Relative Strength Index (RSI)
def compute_rsi(series, window=14):
    """
    RSI hesaplaması:
    - 'series': fiyat serisi (örneğin, kapanış fiyatları)
    - 'window': RSI hesaplamasında kullanılan pencere boyutu (varsayılan 14 gün)
    """
    delta = series.diff()
    # Yalnızca kazanç ve kayıpları ayrı ayrı hesaplayalım
    gain = delta.clip(lower=0)
    loss = -delta.clip(upper=0)

    # Basit hareketli ortalama ile hesaplama (alternatif olarak EWMA da kullanılabilir)
    avg_gain = gain.rolling(window=window, min_periods=window).mean()
    avg_loss = loss.rolling(window=window, min_periods=window).mean()

    RS = avg_gain / avg_loss
    RSI = 100 - (100 / (1 + RS))
    return RSI

def prepare_time_series_data_dev(ticker, start_date="7y"):
    stock = yf.Ticker(ticker)
    df = stock.history(period=start_date)
    if df.empty:
        raise ValueError(f"{ticker} için veri alınamadı. Lütfen geçerli bir hisse sembolü girin.")

    df = df.reset_index()
    df["Date"] = pd.to_datetime(df["Date"]).dt.date
    df['Date'] = pd.to_datetime(df['Date'], errors='coerce')
    df['Close'] = pd.to_numeric(df['Close'], errors='coerce')

    # Feature Engineering
    df["Percentage_Change"] = df['Close'].pct_change()
    df['Volume_Percentage_Change'] = df['Volume'].pct_change()
    df.dropna(inplace=True)

    df['MA_5'] = df['Close'].rolling(window=5).mean()
    df['MA_21'] = df['Close'].rolling(window=21).mean()
    df['MA_63'] = df['Close'].rolling(window=63).mean()
    df['MA_126'] = df['Close'].rolling(window=126).mean()
    df['MA_252'] = df['Close'].rolling(window=252).mean()
    df['EWMA_5'] = df['Close'].ewm(span=5, adjust=False).mean()
    df['EWMA_21'] = df['Close'].ewm(span=21, adjust=False).mean()
    df['EWMA_63'] = df['Close'].ewm(span=63, adjust=False).mean()
    df['EWMA_126'] = df['Close'].ewm(span=126, adjust=False).mean()
    df['EWMA_252'] = df['Close'].ewm(span=252, adjust=False).mean()

    df['Rolling_std_5']  = df['Close'].rolling(window=5).std()
    df['Rolling_std_21'] = df['Close'].rolling(window=21).std()
    df['Rolling_std_63'] = df['Close'].rolling(window=63).std()
    df['Rolling_std_126'] = df['Close'].rolling(window=126).std()
    df['Rolling_std_252'] = df['Close'].rolling(window=252).std()

    df['RSI_5'] = compute_rsi(df['Close'], window=5)
    df['RSI_21'] = compute_rsi(df['Close'], window=21)
    df['RSI_63'] = compute_rsi(df['Close'], window=63)
    df['RSI_126'] = compute_rsi(df['Close'], window=126)
    df['RSI_252'] = compute_rsi(df['Close'], window=252)

    #Farklar (Differencing)
    #Trend bileşenini azaltmak için bir önceki gün ile farkı alıyoruz
    df["Diff"] = df["Close"] - df["Close"].shift(1)

    #Sonsuz (inf) değerleri kontrol et ve NaN'a çevir
    df.replace([np.inf, -np.inf], np.nan, inplace=True)

    #NaN değerleri önceki ve sonraki değerlerin ortalamasıyla doldur
    df = df.interpolate(method='linear', limit_direction='both')

    #!!!!
    max_window = 252
    df = df.iloc[max_window:]

    df = df.drop(columns=["Open", "High", "Low", "Volume", "Dividends", "Stock Splits"], axis=1)
    df.dropna(inplace=True)
    df = df.reset_index(drop=True)
    return df

In [ ]:
df_bax = prepare_time_series_data_dev("BAX")

In [ ]:
df_bax.head(5)

Date      Close  Percentage_Change  Volume_Percentage_Change  \
0 2019-02-05  64.491371          -0.007165                  0.028984   
1 2019-02-06  64.240723          -0.003887                 -0.233413   
2 2019-02-07  63.649971          -0.009196                  0.074415   
3 2019-02-08  63.999054           0.005484                  0.166190   
4 2019-02-11  64.204933           0.003217                 -0.315157   

        MA_5      MA_21      MA_63     MA_126     MA_252     EWMA_5  ...  \
0  64.618445  62.060963  59.478401  62.255494  62.203869  64.385874  ...   
1  64.627399  62.299654  59.617121  62.252925  62.228472  64.337490  ...   
2  64.380354  62.517886  59.741931  62.245526  62.246688  64.108317  ...   
3  64.267578  62.704576  59.859105  62.239979  62.270226  64.071896  ...   
4  64.117210  62.892972  59.978556  62.240306  62.305092  64.116242  ...   

   Rolling_std_21  Rolling_std_63  Rolling_std_126  Rolling_std_252  \
0        1.975472        2.554510         3.989089         3.698215   
1        1.918075        2.572286         3.987694         3.691026   
2        1.788212        2.574205         3.984201         3.686649   
3        1.724322        2.597574         3.981244         3.678787   
4        1.657403        2.621917         3.981405         3.655152   

       RSI_5     RSI_21     RSI_63    RSI_126    RSI_252      Diff  
0  75.281418  71.330007  58.553503  50.045942  51.154713 -0.465401  
1  51.055191  71.605034  59.225718  49.810193  51.929566 -0.250648  
2  19.468970  69.047713  58.247454  49.457029  51.432473 -0.590752  
3  36.244933  67.244149  57.821833  49.594034  51.858466  0.349083  
4  29.808421  67.347062  57.949621  50.023986  52.795637  0.205879  

[5 rows x 25 columns]

# `dataframes_dev` dict (`prepare_time_series_data_dev` ile çekilmiş veriler)

In [ ]:
# Sözlükte verileri saklamak için bir boş sözlük oluşturuyoruz
dataframes_dev = {}

# Döngüyle her şirketin verisini çekiyoruz
for ticker in tickers_inf:
    try:
        print(f"{ticker} verileri çekiliyor...")
        dataframes_dev[ticker] = prepare_time_series_data_dev(ticker)
        print(f"{ticker} verileri başarıyla çekildi.")
    except Exception as e:
        print(f"{ticker} verileri alınamadı: {e}")

MMM verileri çekiliyor...
MMM verileri başarıyla çekildi.
AOS verileri çekiliyor...
AOS verileri başarıyla çekildi.
ABT verileri çekiliyor...
ABT verileri başarıyla çekildi.
ABBV verileri çekiliyor...
ABBV verileri başarıyla çekildi.
ACN verileri çekiliyor...
ACN verileri başarıyla çekildi.
ADBE verileri çekiliyor...
ADBE verileri başarıyla çekildi.
AMD verileri çekiliyor...
AMD verileri başarıyla çekildi.
AES verileri çekiliyor...
AES verileri başarıyla çekildi.
AFL verileri çekiliyor...
AFL verileri başarıyla çekildi.
A verileri çekiliyor...
A verileri başarıyla çekildi.
APD verileri çekiliyor...
APD verileri başarıyla çekildi.
ABNB verileri çekiliyor...
ABNB verileri başarıyla çekildi.
AKAM verileri çekiliyor...
AKAM verileri başarıyla çekildi.
ALB verileri çekiliyor...
ALB verileri başarıyla çekildi.
ARE verileri çekiliyor...
ARE verileri başarıyla çekildi.
ALGN verileri çekiliyor...
ALGN verileri başarıyla çekildi.
ALLE verileri çekiliyor...
ALLE verileri başarıyla çekildi.
LNT ve

In [ ]:
# Pickle dosyası olarak kaydet
with open("dataframes_dev.pkl", "wb") as file:
    pickle.dump(dataframes_dev, file)

# Yeni Veriler ile ML Modeli Eğitimi (`evaluate_models_wf_dev_2`)

## Regresyon Modelleri

In [ ]:
regression_models = {
    "DecisionTree": DecisionTreeRegressor(),
    "RandomForest": RandomForestRegressor(),
    "GradientBoosting": GradientBoostingRegressor(),
    "AdaBoost": AdaBoostRegressor(),
    "KNN": KNeighborsRegressor(),
    "LinearRegression": LinearRegression(),
    "LassoRegression": Lasso(),
    "RidgeRegression": Ridge(),
    "LinearSVR": SVR(kernel="linear"),
    "RbfSVR": SVR(kernel="rbf"),
    "PolynomialSVR": SVR(kernel="poly"),
    "XGBoost": xgb.XGBRegressor()
}

## `evalute_models_dev` (PCA ile)

In [ ]:
df_bax = prepare_time_series_data_dev("BAX")

In [ ]:
df_bax.columns

Index(['Date', 'Close', 'Percentage_Change', 'Volume_Percentage_Change',
       'MA_5', 'MA_21', 'MA_63', 'MA_126', 'MA_252', 'EWMA_5', 'EWMA_21',
       'EWMA_63', 'EWMA_126', 'EWMA_252', 'Rolling_std_5', 'Rolling_std_21',
       'Rolling_std_63', 'Rolling_std_126', 'Rolling_std_252', 'RSI_5',
       'RSI_21', 'RSI_63', 'RSI_126', 'RSI_252', 'Diff'],
      dtype='object')

In [ ]:
df_bax.shape

(2012, 25)

In [ ]:
def evaluate_models_dev(stock_names=list()):
    # Beklenen sütunların listesi
    required_columns = ['Date', 'Close', 'Percentage_Change', 'Volume_Percentage_Change',
       'MA_5', 'MA_21', 'MA_63', 'MA_126', 'MA_252', 'EWMA_5', 'EWMA_21',
       'EWMA_63', 'EWMA_126', 'EWMA_252', 'Rolling_std_5', 'Rolling_std_21',
       'Rolling_std_63', 'Rolling_std_126', 'Rolling_std_252', 'RSI_5',
       'RSI_21', 'RSI_63', 'RSI_126', 'RSI_252', 'Diff']

    for ticker in stock_names:
        if ticker in dataframes_dev:
            print(f"\n=== {ticker} için Model Performansı Sonuçları ===")

            df = dataframes_dev[ticker]

            # Veri çerçevesi boş mu kontrol et
            if df.empty:
                print(f"{ticker} için veri çerçevesi boş, atlanıyor.")
                continue

            # Eksik sütunları kontrol et
            missing_columns = [col for col in required_columns if col not in df.columns]
            if missing_columns:
                print(f"{ticker} için eksik sütunlar: {missing_columns}, atlanıyor.")
                continue

            try:
                # X ve y ayrımı
                X = df.drop(columns=["Date", "Close"], axis=1)
                y = df["Close"]

                # Standartlaştırma
                X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=False)
                scaler = StandardScaler()
                X_train_scaled = scaler.fit_transform(X_train)
                X_test_scaled = scaler.transform(X_test)

                # PCA Uygulanması
                pca = PCA(n_components=0.95)  # Varyansın %95'ini açıklayan bileşenler seçiliyor
                X_train_pca = pca.fit_transform(X_train_scaled)
                X_test_pca = pca.transform(X_test_scaled)

                for name, reg in regression_models.items():
                    try:
                        reg.fit(X_train_pca, y_train)
                        predictions = reg.predict(X_test_pca)
                        train_score = reg.score(X_train_pca, y_train)
                        test_score = reg.score(X_test_pca, y_test)
                        mse = mean_squared_error(y_test, predictions)
                        mae = mean_absolute_error(y_test, predictions)
                        r2 = r2_score(y_test, predictions)

                        # Ek regresyon metrikleri: RMSE, MAPE ve sMAPE
                        rmse = np.sqrt(mse)
                        mape = np.mean(np.abs((y_test - predictions) / y_test)) * 100
                        smape = np.mean(2 * np.abs(y_test - predictions) / (np.abs(y_test) + np.abs(predictions))) * 100

                        print(f"\nModel: {name}")
                        print(f"Train Setindeki Doğruluk: {train_score}")
                        print(f"Test Setindeki Doğruluk: {test_score}")
                        print(f"MSE Skoru: {mse}")
                        print(f"MAE Skoru: {mae}")
                        print(f"RMSE Skoru: {rmse}")
                        print(f"MAPE Skoru: {mape}")
                        print(f"sMAPE Skoru: {smape}")
                        print(f"R^2 Skoru: {r2}")

                        # (Burada sınıflandırma metrikleri, backtesting ve diğer finansal metrikler mevcutsa eklenebilir.)

                    except Exception as e:
                        print(f"{name} modeli {ticker} için hata verdi: {e}")

            except Exception as e:
                print(f"{ticker} için bir hata oluştu: {e}")
        else:
            print(f"\nTicker {ticker} not found in dataframes_inf, skipping...")  # Ticker bulunamazsa mesaj yazdır


In [ ]:
evaluate_models_dev(stock_names = ["BAX"])


=== BAX için Model Performansı Sonuçları ===

Model: DecisionTree
Train Setindeki Doğruluk: 1.0
Test Setindeki Doğruluk: -1.3697430883640713
MSE Skoru: 35.85157567471065
MAE Skoru: 5.1724175199977225
RMSE Skoru: 5.987618531161671
MAPE Skoru: 15.112482830882087
sMAPE Skoru: 13.664427258221249
R^2 Skoru: -1.3697430883640713

Model: RandomForest
Train Setindeki Doğruluk: 0.9992212422130619
Test Setindeki Doğruluk: -1.3531574708738083
MSE Skoru: 35.6006537399728
MAE Skoru: 5.223677973120148
RMSE Skoru: 5.966628339353206
MAPE Skoru: 15.237582447648274
sMAPE Skoru: 13.798024815952136
R^2 Skoru: -1.3531574708738083

Model: GradientBoosting
Train Setindeki Doğruluk: 0.9971281577951822
Test Setindeki Doğruluk: -0.5308569280989
MSE Skoru: 23.160161653971176
MAE Skoru: 4.263493719634008
RMSE Skoru: 4.812500561451518
MAPE Skoru: 12.350712341912182
sMAPE Skoru: 11.414096204956486
R^2 Skoru: -0.5308569280989

Model: AdaBoost
Train Setindeki Doğruluk: 0.9724808366707289
Test Setindeki Doğruluk: -2.5

## Walk-Farward Validation (`evaluate_models_dev_wf`) (PCA ile)

---



In [ ]:
def walk_forward_validation_pretrained(df, model, scaler, pca, n_test):
    """
    Parametreler:
        df: Şirketin tüm verisini içeren DataFrame (tarihsel veriler)
        model: Önceden eğitilmiş model (train set üzerinde eğitilmiş)
        scaler: Train set üzerinden fit edilmiş StandardScaler nesnesi
        pca: Train set üzerinden fit edilmiş PCA nesnesi
        n_test: Walk-forward validation için kullanılacak test periyodundaki gözlem sayısı (örneğin, 5, 20, 60, 120, 252)

    Fonksiyon, belirtilen n_test periyodu için, pre-trained model kullanarak
    walk-forward tahminlerini yapar ve RMSE, MAPE, sMAPE metriklerini döndürür.
    """
    wf_predictions = []
    wf_actuals = []
    test_wf = df.iloc[-n_test:].copy()

    # Pre-trained scaler ve PCA, modelin eğitiminde kullanılan nesnelerdir.
    # Bu nesnelerle, test verisindeki her bir yeni gözlemin dönüşümünü yapıyoruz.
    for i in range(len(test_wf)):
        row = test_wf.iloc[i]
        X_new = row.drop(labels=["Date", "Close"]).to_frame().T
        # Özellik isimlerini koruyarak scaler ve PCA dönüşümleri uyguluyoruz.
        X_new_scaled = scaler.transform(X_new)
        X_new_pca = pca.transform(X_new_scaled)
        yhat = model.predict(X_new_pca)[0]
        wf_predictions.append(yhat)
        wf_actuals.append(row["Close"])

    wf_mse = mean_squared_error(wf_actuals, wf_predictions)
    wf_rmse = np.sqrt(wf_mse)
    wf_mape = np.mean(np.abs((np.array(wf_actuals) - np.array(wf_predictions)) / np.array(wf_actuals))) * 100
    wf_smape = np.mean(2 * np.abs(np.array(wf_actuals) - np.array(wf_predictions)) /
                        (np.abs(np.array(wf_actuals)) + np.abs(np.array(wf_predictions)))) * 100
    return wf_rmse, wf_mape, wf_smape


In [ ]:
def evaluate_models_dev_wf(stock_names=list()):
    # Beklenen sütunların listesi
    required_columns = ['Date', 'Close', 'Percentage_Change', 'Volume_Percentage_Change',
                        'MA_5', 'MA_21', 'MA_63', 'MA_126', 'MA_252', 'EWMA_5', 'EWMA_21',
                        'EWMA_63', 'EWMA_126', 'EWMA_252', 'Rolling_std_5', 'Rolling_std_21',
                        'Rolling_std_63', 'Rolling_std_126', 'Rolling_std_252', 'RSI_5',
                        'RSI_21', 'RSI_63', 'RSI_126', 'RSI_252', 'Diff']

    # Tanımlı walk-forward periyotları (trading günleri bazında)
    horizons = {'1 hafta': 5, '1 ay': 21, '3 ay': 63, '6 ay': 126, '1 yıl': 252}

    for ticker in stock_names:
        if ticker in dataframes_dev:
            print(f"\n=== {ticker} için Model Performansı Sonuçları ===")
            df = dataframes_dev[ticker]

            # Veri çerçevesi boş mu kontrol et
            if df.empty:
                print(f"{ticker} için veri çerçevesi boş, atlanıyor.")
                continue

            # Eksik sütunları kontrol et
            missing_columns = [col for col in required_columns if col not in df.columns]
            if missing_columns:
                print(f"{ticker} için eksik sütunlar: {missing_columns}, atlanıyor.")
                continue

            try:
                # X ve y ayrımı
                X = df.drop(columns=["Date", "Close"], axis=1)
                y = df["Close"]

                # Sabit train-test bölmesi
                X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=False)
                scaler = StandardScaler()
                X_train_scaled = scaler.fit_transform(X_train)
                X_test_scaled = scaler.transform(X_test)

                pca = PCA(n_components=0.95)  # Varyansın %95'ini açıklayan bileşenler seçiliyor
                X_train_pca = pca.fit_transform(X_train_scaled)
                X_test_pca = pca.transform(X_test_scaled)

                for name, reg in regression_models.items():
                    try:
                        # Sabit train-test split ile eğitim ve tahmin
                        reg.fit(X_train_pca, y_train)
                        predictions = reg.predict(X_test_pca)
                        train_score = reg.score(X_train_pca, y_train)
                        test_score = reg.score(X_test_pca, y_test)
                        mse = mean_squared_error(y_test, predictions)
                        mae = mean_absolute_error(y_test, predictions)
                        r2 = r2_score(y_test, predictions)

                        # Ek regresyon metrikleri: RMSE, MAPE ve sMAPE
                        rmse = np.sqrt(mse)
                        mape = np.mean(np.abs((y_test - predictions) / y_test)) * 100
                        smape = np.mean(2 * np.abs(y_test - predictions) / (np.abs(y_test) + np.abs(predictions))) * 100

                        print(f"\nModel: {name}")
                        print(f"Train Setindeki Doğruluk: {train_score}")
                        print(f"Test Setindeki Doğruluk: {test_score}")
                        print(f"MSE Skoru: {mse}")
                        print(f"MAE Skoru: {mae}")
                        print(f"RMSE Skoru: {rmse}")
                        print(f"MAPE Skoru: {mape}")
                        print(f"sMAPE Skoru: {smape}")
                        print(f"R^2 Skoru: {r2}")

                        # Pre-trained model, scaler ve PCA zaten oluşturulmuş durumda.
                        # Bu nesneler, sabit train-test split ile model eğitimi sırasında elde edildi.
                        print("Walk-forward Validation (Pre-trained Model) Sonuçları:")
                        for horizon_name, n_test in horizons.items():
                            wf_rmse, wf_mape, wf_smape = walk_forward_validation_pretrained(df, reg, scaler, pca, n_test)
                            print(f"{horizon_name} Walk-forward Validation - RMSE: {wf_rmse}, MAPE: {wf_mape}, sMAPE: {wf_smape}")

                    except Exception as e:
                        print(f"{name} modeli {ticker} için hata verdi: {e}")

            except Exception as e:
                print(f"{ticker} için bir hata oluştu: {e}")

        else:
            print(f"\nTicker {ticker} not found in dataframes_inf, skipping...")


In [ ]:
evaluate_models_dev_wf(["BAX"])


=== BAX için Model Performansı Sonuçları ===

Model: DecisionTree
Train Setindeki Doğruluk: 1.0
Test Setindeki Doğruluk: -1.6031860729330498
MSE Skoru: 39.383308235974376
MAE Skoru: 5.500922550930278
RMSE Skoru: 6.27561218017608
MAPE Skoru: 16.01004166827148
sMAPE Skoru: 14.435197537591621
R^2 Skoru: -1.6031860729330498
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 9.673078591382074, MAPE: 29.347049788864886, sMAPE: 25.58057043709222
1 ay Walk-forward Validation - RMSE: 10.641221768161358, MAPE: 34.3258201167587, sMAPE: 29.25623725428278
3 ay Walk-forward Validation - RMSE: 10.051310681276208, MAPE: 31.416687980494867, sMAPE: 26.944285174661264
6 ay Walk-forward Validation - RMSE: 8.092181473228099, MAPE: 22.97262550867784, sMAPE: 20.213695414865
1 yıl Walk-forward Validation - RMSE: 6.933087054576045, MAPE: 18.146850280752087, sMAPE: 16.17793144994763

Model: RandomForest
Train Setindeki Doğruluk: 0.9992302860182548
Test Setindeki Doğr

## `evalute_models_dev_wf_2` (PLSRegression İle) + (Regresyon tabanlı modellerde iyi sonuç veren şirket üzerinde)

+ `PLSRegression`, Çoklu Lineer Regresyon ile PCA'nın birleşiminden oluşan bir yöntemdir. PCA, temel olarak veri setindeki varyansı maksimize eden doğrusal kombinasyonlar oluşturuyor ancak bu dönüşüm zaman serisinin ardışıklığını ve dinamiklerini göz önüne almıyor. Bundan dolayı zaman serisi analizinde PCA kullanmak riskli olabilir. Bu yüzden de ne yapabileceğimi araştırdım ve PLSRegression adlı bu yöntemi buldum. Bu yöntem:

  + PLS, öznitelikler arasındaki korelasyonu azaltırken aynı zamanda bağımlı değişken (örneğin, fiyat) ile öznitelikler arasındaki ilişkiyi maksimize etmeye çalışır. Bu sayede, boyut indirgeme yaparken hedef değişkenle olan ilişkiyi de korur ve zaman serilerinde uygulandığında daha anlamlı özetler elde edilebilir. Böylece hem multikolinearitenin önüne geçmiş olacağım hem de zaman serisinin ardışıklığını da göz önüne alan bir yöntem kullanmış olacağım.

In [ ]:
def walk_forward_validation_pretrained(df, model, scaler, pca, n_test):
    """
    Parametreler:
        df: Şirketin tüm verisini içeren DataFrame (tarihsel veriler)
        model: Önceden eğitilmiş model (train set üzerinde eğitilmiş)
        scaler: Train set üzerinden fit edilmiş StandardScaler nesnesi
        pca: Train set üzerinden fit edilmiş PCA nesnesi
        n_test: Walk-forward validation için kullanılacak test periyodundaki gözlem sayısı (örneğin, 5, 20, 60, 120, 252)

    Fonksiyon, belirtilen n_test periyodu için, pre-trained model kullanarak
    walk-forward tahminlerini yapar ve RMSE, MAPE, sMAPE metriklerini döndürür.
    """
    wf_predictions = []
    wf_actuals = []
    test_wf = df.iloc[-n_test:].copy()

    # Pre-trained scaler ve PCA, modelin eğitiminde kullanılan nesnelerdir.
    # Bu nesnelerle, test verisindeki her bir yeni gözlemin dönüşümünü yapıyoruz.
    for i in range(len(test_wf)):
        row = test_wf.iloc[i]
        X_new = row.drop(labels=["Date", "Close"]).to_frame().T
        # Özellik isimlerini koruyarak scaler ve PCA dönüşümleri uyguluyoruz.
        X_new_scaled = scaler.transform(X_new)
        X_new_pca = pca.transform(X_new_scaled)
        yhat = model.predict(X_new_pca)[0]
        wf_predictions.append(yhat)
        wf_actuals.append(row["Close"])

    wf_mse = mean_squared_error(wf_actuals, wf_predictions)
    wf_rmse = np.sqrt(wf_mse)
    wf_mape = np.mean(np.abs((np.array(wf_actuals) - np.array(wf_predictions)) / np.array(wf_actuals))) * 100
    wf_smape = np.mean(2 * np.abs(np.array(wf_actuals) - np.array(wf_predictions)) /
                        (np.abs(np.array(wf_actuals)) + np.abs(np.array(wf_predictions)))) * 100
    return wf_rmse, wf_mape, wf_smape


In [ ]:
from sklearn.cross_decomposition import PLSRegression

def evaluate_models_dev_wf_2(stock_names=list()):
    # Beklenen sütunların listesi
    required_columns = ['Date', 'Close', 'Percentage_Change', 'Volume_Percentage_Change',
                        'MA_5', 'MA_21', 'MA_63', 'MA_126', 'MA_252', 'EWMA_5', 'EWMA_21',
                        'EWMA_63', 'EWMA_126', 'EWMA_252', 'Rolling_std_5', 'Rolling_std_21',
                        'Rolling_std_63', 'Rolling_std_126', 'Rolling_std_252', 'RSI_5',
                        'RSI_21', 'RSI_63', 'RSI_126', 'RSI_252', 'Diff']

    # Tanımlı walk-forward periyotları (trading günleri bazında)
    horizons = {'1 hafta': 5, '1 ay': 21, '3 ay': 63, '6 ay': 126, '1 yıl': 252}

    for ticker in stock_names:
        if ticker in dataframes_dev:
            print(f"\n=== {ticker} için Model Performansı Sonuçları ===")
            df = dataframes_dev[ticker]

            # Veri çerçevesi boş mu kontrol et
            if df.empty:
                print(f"{ticker} için veri çerçevesi boş, atlanıyor.")
                continue

            # Eksik sütunları kontrol et
            missing_columns = [col for col in required_columns if col not in df.columns]
            if missing_columns:
                print(f"{ticker} için eksik sütunlar: {missing_columns}, atlanıyor.")
                continue

            try:
                # X ve y ayrımı
                X = df.drop(columns=["Date", "Close"], axis=1)
                y = df["Close"]

                # Sabit train-test bölmesi
                X_train, X_test, y_train, y_test = train_test_split(
                    X, y, test_size=0.2, random_state=42, shuffle=False
                )
                scaler = StandardScaler()
                X_train_scaled = scaler.fit_transform(X_train)
                X_test_scaled = scaler.transform(X_test)

                # PCA yerine PLS regresyonu uyguluyoruz.
                # n_components, öznitelik sayınızın küçük bir kısmı veya sabit bir değer olabilir.
                n_components = min(10, X_train_scaled.shape[1])
                pls = PLSRegression(n_components=n_components)
                # fit_transform dönen değerin ilk kısmı, X üzerindeki latent bileşenlerdir.
                X_train_pls, _ = pls.fit_transform(X_train_scaled, y_train)
                X_test_pls = pls.transform(X_test_scaled)

                for name, reg in regression_models.items():
                    try:
                        # Sabit train-test split ile eğitim ve tahmin
                        reg.fit(X_train_pls, y_train)
                        predictions = reg.predict(X_test_pls)
                        train_score = reg.score(X_train_pls, y_train)
                        test_score = reg.score(X_test_pls, y_test)
                        mse = mean_squared_error(y_test, predictions)
                        mae = mean_absolute_error(y_test, predictions)
                        r2 = r2_score(y_test, predictions)

                        # Ek regresyon metrikleri: RMSE, MAPE ve sMAPE
                        rmse = np.sqrt(mse)
                        mape = np.mean(np.abs((y_test - predictions) / y_test)) * 100
                        smape = np.mean(2 * np.abs(y_test - predictions) / (np.abs(y_test) + np.abs(predictions))) * 100

                        print(f"\nModel: {name}")
                        print(f"Train Setindeki Doğruluk: {train_score}")
                        print(f"Test Setindeki Doğruluk: {test_score}")
                        print(f"MSE Skoru: {mse}")
                        print(f"MAE Skoru: {mae}")
                        print(f"RMSE Skoru: {rmse}")
                        print(f"MAPE Skoru: {mape}")
                        print(f"sMAPE Skoru: {smape}")
                        print(f"R^2 Skoru: {r2}")

                        # Pre-trained model, scaler ve PLS (dimensionality reduction) zaten oluşturulmuş durumda.
                        print("Walk-forward Validation (Pre-trained Model) Sonuçları:")
                        for horizon_name, n_test in horizons.items():
                            # Walk-forward validation fonksiyonunda artık 'pca' yerine 'pls' objesi kullanılıyor.
                            wf_rmse, wf_mape, wf_smape = walk_forward_validation_pretrained(
                                df, reg, scaler, pls, n_test
                            )
                            print(f"{horizon_name} Walk-forward Validation - RMSE: {wf_rmse}, MAPE: {wf_mape}, sMAPE: {wf_smape}")

                    except Exception as e:
                        print(f"{name} modeli {ticker} için hata verdi: {e}")

            except Exception as e:
                print(f"{ticker} için bir hata oluştu: {e}")

        else:
            print(f"\nTicker {ticker} not found in dataframes_inf, skipping...")


In [ ]:
evaluate_models_dev_wf_2(["BAX"])


=== BAX için Model Performansı Sonuçları ===

Model: DecisionTree
Train Setindeki Doğruluk: 1.0
Test Setindeki Doğruluk: 0.6284770950600451
MSE Skoru: 4.099128658614388
MAE Skoru: 1.6272321094740305
RMSE Skoru: 2.024630499279903
MAPE Skoru: 4.611245251831564
sMAPE Skoru: 4.474861162431608
R^2 Skoru: 0.6284770950600451
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 1.5020577785909417, MAPE: 4.387050177207398, sMAPE: 4.286171692042724
1 ay Walk-forward Validation - RMSE: 2.1762920316762986, MAPE: 6.515127477621453, sMAPE: 6.26686399128929
3 ay Walk-forward Validation - RMSE: 2.3929517819908406, MAPE: 6.846295713800027, sMAPE: 6.570378066771088
6 ay Walk-forward Validation - RMSE: 2.4997523545791003, MAPE: 6.211870440494216, sMAPE: 5.957818496000895
1 yıl Walk-forward Validation - RMSE: 2.0334926475615145, MAPE: 4.615010548778202, sMAPE: 4.4744070620184235

Model: RandomForest
Train Setindeki Doğruluk: 0.9996284246122026
Test Setindeki Doğr

Çok önemli bir sonuç elde ettim. Şimdi, PCA ile boyutu azaltılmış **LinearSVR** modelinin sonuçlarını ve PLSRegression ile boyutu azaltılmış **LinearSVR** modelinin sonuçlarına bakalım ve farkı görelim:

+ **PCA ile LinearSVR**

Model: LinearSVR

Train Setindeki Doğruluk: 0.9927889296474803

**``Test Setindeki Doğruluk: 0.6762525546675504``**

MSE Skoru: 4.897938554108515

MAE Skoru: 2.0563199207915273

RMSE Skoru: 2.2131286799706236

MAPE Skoru: 5.833934133902006

sMAPE Skoru: 6.05053984829322

R^2 Skoru: 0.6762525546675504

Walk-forward Validation (Pre-trained Model) Sonuçları:

1 hafta Walk-forward Validation - RMSE: 1.490828155515524, MAPE: 4.4187371863353935, sMAPE: 4.52455494233011

1 ay Walk-forward Validation - RMSE: 2.382643855346839, MAPE: 7.338741181541569, sMAPE: 7.665909154325432

3 ay Walk-forward Validation - RMSE: 2.5494815650498786, MAPE: 7.796690413666507, sMAPE: 8.150756011555368

6 ay Walk-forward Validation - RMSE: 2.3282541636022014, MAPE: 6.6019033451069316, sMAPE: 6.86303662542078

1 yıl Walk-forward Validation - RMSE: 2.3024537004949104, MAPE: 6.2081323248568365, sMAPE: 6.4510571278978235

+ **PLSRegression ile LinearSVR**

Model: LinearSVR

Train Setindeki Doğruluk: 0.9976336897784427

**``Test Setindeki Doğruluk: 0.9880556474648343``**

MSE Skoru: 0.1807047611627526

MAE Skoru: 0.34369216259226154

RMSE Skoru: 0.42509382630514947

MAPE Skoru: 0.9564006682145264

sMAPE Skoru: 0.9585222799883075

R^2 Skoru: 0.9880556474648343

Walk-forward Validation (Pre-trained Model) Sonuçları:

1 hafta Walk-forward Validation - RMSE: 0.21695626977578197, MAPE: 0.588727241278118, sMAPE: 0.5865467980144802

1 ay Walk-forward Validation - RMSE: 0.31851840671245835, MAPE: 0.8643863067020865, sMAPE: 0.8656450234450483

3 ay Walk-forward Validation - RMSE: 0.393387939717609, MAPE: 0.9931429536669029, sMAPE: 0.9993491364773115

6 ay Walk-forward Validation - RMSE: 0.41930234452450366, MAPE: 0.9983255521392534, sMAPE: 1.0021746757354657

1 yıl Walk-forward Validation - RMSE: 0.4114383725485295, MAPE: 0.9409483972727771, sMAPE: 0.9451481684604435

+ PCA ve PLS ile boyutu azaltılarak eğitilen modellerin sonuçları arasında önemli bir fark var. PCA'daki overfitting, PLS uygulandıktan sonra ortadan kalkıyor ve diğer sonuçları negatif olarak etkilemeden test setindeki tahmin doğruluğunu arttırıyor. 'BAX' kodlu şirket, `prepare_time_series_data_inf` ile verileri çekildiğinde ve `evaluate_models` ile eğitildiğinde negatif test seti sonuçları verirken; `prepare_time_series_data_dev` ile verileri çekilip `evaluate_models_dev` ile eğitildiğinde %60 oranlarında test seti doğruluğu vermişti. PLS uygulandığında da bu sonuç %98'e çıktı.

+ Benim merak ettiğim; PLS çoklu regresyon ve PCA'nın birleşimi olduğundan, acaba yalnızca regresyon tabanlı modellerde mi bu şekilde bir performans artışı sağlacak yoksa ağaç tabanlı modellerde daha iyi sonuçlar veren şirketler için de aynı performans artışını sağlayacak mı? Bunu deneyeceğim.

## `evaluate_models_dev_wf_2` (PLSRegression ile) + (Ağaç Tabanlı Modellerde iyi sonuç veren şirket ile)

+ `'GPN'` kodlu şirket, ağaç tabanlı bir model olan `GradientBoosting`'de en iyi sonucu vermiş. Bu sonuç, `prepare_time_series_data_inf` adlı fonksiyon ile yani geliştirme yapılmadan önce ve `PCA` ile boyutu azaltılarak elde edilmişti. Sonuç şu şekildeydi:

Train: 0,98 /
Test: 0,89 /
MSE: 14,3 /
MAE: 3,05 /
R2: 0,89 /
MAPE: 0,02

Şimdi hem geliştirilmiş olan `prepare_time_series_data_dev` ile hazırlanmış veriyi kullanacağım ve boyutu `PLS` metodu ile azaltacağım. Bakalım sonuç ne olacak


In [ ]:
df_gpn = dataframes_dev["GPN"].copy()

In [ ]:
evaluate_models_dev_wf_2(["GPN"])


=== GPN için Model Performansı Sonuçları ===

Model: DecisionTree
Train Setindeki Doğruluk: 1.0
Test Setindeki Doğruluk: 0.9285998317351718
MSE Skoru: 10.802395223505565
MAE Skoru: 2.6103205144010633
RMSE Skoru: 3.286699746479067
MAPE Skoru: 2.311867386477377
sMAPE Skoru: 2.2984804546866884
R^2 Skoru: 0.9285998317351718
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 7.509034590394346, MAPE: 6.491450254408362, sMAPE: 6.292098481769568
1 ay Walk-forward Validation - RMSE: 4.741509646704284, MAPE: 3.5914358711152823, sMAPE: 3.5154755436875282
3 ay Walk-forward Validation - RMSE: 4.191008014163451, MAPE: 3.1259407284161287, sMAPE: 3.074508308521114
6 ay Walk-forward Validation - RMSE: 3.4180494170449194, MAPE: 2.4122448910432452, sMAPE: 2.385688573670238
1 yıl Walk-forward Validation - RMSE: 3.213578683897156, MAPE: 2.270328965478606, sMAPE: 2.2613355380626805

Model: RandomForest
Train Setindeki Doğruluk: 0.9993936513471242
Test Setindeki D

+ Sonuçlara baktığımda Test skoru: 0.89'dan, 0,98'e çıktı ve MSE skoru: 14,3'ten, 6'lara kadar düştü. Yani PLS yalnızca regresyon modellerinde performans artışı sağlamak yerine ağaç tabanlı modellerde iyi sonuç veren şirketlerde de performans artışı sağladı.

In [ ]:
df_moh = dataframes_dev["MOH"].copy()

In [ ]:
evaluate_models_dev_wf_2(["MOH"])


=== MOH için Model Performansı Sonuçları ===

Model: DecisionTree
Train Setindeki Doğruluk: 1.0
Test Setindeki Doğruluk: 0.478523267494521
MSE Skoru: 669.1642475293345
MAE Skoru: 19.970134002483444
RMSE Skoru: 25.868209206076376
MAPE Skoru: 5.617073692881338
sMAPE Skoru: 5.829613548889031
R^2 Skoru: 0.478523267494521
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 15.415902232459057, MAPE: 4.8148537772863484, sMAPE: 4.6940672108771615
1 ay Walk-forward Validation - RMSE: 20.3228745989055, MAPE: 6.144170345130057, sMAPE: 5.921525681454583
3 ay Walk-forward Validation - RMSE: 14.280756381071594, MAPE: 3.6328721707024525, sMAPE: 3.544701101165225
6 ay Walk-forward Validation - RMSE: 16.06718672214861, MAPE: 4.045417010880338, sMAPE: 4.064213888565177
1 yıl Walk-forward Validation - RMSE: 27.424380850417684, MAPE: 5.9875576595796325, sMAPE: 6.223442496345001

Model: RandomForest
Train Setindeki Doğruluk: 0.9997105327470768
Test Setindeki Doğr

+ `MOH` kodlu şirket ise en iyi sonucu RidgeRegression'da vermişti ancak o sonuçta bile overfitting mevcuttu ayrıca MSE skoru: 477,54 idi. Bu sonuçta ise hem test setindeki skoru 0,57'den, 0,98' çıktı hem de MSE skoru: 19'a düştü.

# ``evaluate_models_dev_wf_3`` (Çıktı Sonuçlarını Bir DataFrame'e Kaydetmek İçin)

## Kod Bloğu ve Ufak Deneme

In [ ]:
from sklearn.cross_decomposition import PLSRegression
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

def evaluate_models_dev_wf_3(stock_names=list()):
    results = []  # Sonuçları saklamak için boş liste

    # Beklenen sütunların listesi
    required_columns = ['Date', 'Close', 'Percentage_Change', 'Volume_Percentage_Change',
                        'MA_5', 'MA_21', 'MA_63', 'MA_126', 'MA_252', 'EWMA_5', 'EWMA_21',
                        'EWMA_63', 'EWMA_126', 'EWMA_252', 'Rolling_std_5', 'Rolling_std_21',
                        'Rolling_std_63', 'Rolling_std_126', 'Rolling_std_252', 'RSI_5',
                        'RSI_21', 'RSI_63', 'RSI_126', 'RSI_252', 'Diff']

    # Tanımlı walk-forward periyotları (trading günleri bazında)
    horizons = {'1 hafta': 5, '1 ay': 21, '3 ay': 63, '6 ay': 126, '1 yıl': 252}

    for ticker in stock_names:
        if ticker in dataframes_dev:
            print(f"\n=== {ticker} için Model Performansı Sonuçları ===")
            df = dataframes_dev[ticker]

            # Veri çerçevesi boş mu kontrol et
            if df.empty:
                print(f"{ticker} için veri çerçevesi boş, atlanıyor.")
                continue

            # Eksik sütunları kontrol et
            missing_columns = [col for col in required_columns if col not in df.columns]
            if missing_columns:
                print(f"{ticker} için eksik sütunlar: {missing_columns}, atlanıyor.")
                continue

            try:
                # X ve y ayrımı
                X = df.drop(columns=["Date", "Close"], axis=1)
                y = df["Close"]

                # Sabit train-test bölmesi
                X_train, X_test, y_train, y_test = train_test_split(
                    X, y, test_size=0.2, random_state=42, shuffle=False
                )
                scaler = StandardScaler()
                X_train_scaled = scaler.fit_transform(X_train)
                X_test_scaled = scaler.transform(X_test)

                # PCA yerine PLS regresyonu uyguluyoruz.
                n_components = min(10, X_train_scaled.shape[1])
                pls = PLSRegression(n_components=n_components)
                # fit_transform dönen ilk değer, X üzerindeki latent bileşenlerdir.
                X_train_pls, _ = pls.fit_transform(X_train_scaled, y_train)
                X_test_pls = pls.transform(X_test_scaled)

                for name, reg in regression_models.items():
                    try:
                        # Sabit train-test split ile eğitim ve tahmin
                        reg.fit(X_train_pls, y_train)
                        predictions = reg.predict(X_test_pls)
                        train_score = reg.score(X_train_pls, y_train)
                        test_score = reg.score(X_test_pls, y_test)
                        mse = mean_squared_error(y_test, predictions)
                        mae = mean_absolute_error(y_test, predictions)
                        r2 = r2_score(y_test, predictions)
                        rmse = np.sqrt(mse)
                        mape = np.mean(np.abs((y_test - predictions) / y_test)) * 100
                        smape = np.mean(2 * np.abs(y_test - predictions) / (np.abs(y_test) + np.abs(predictions))) * 100

                        print(f"\nModel: {name}")
                        print(f"Train Setindeki Doğruluk: {train_score}")
                        print(f"Test Setindeki Doğruluk: {test_score}")
                        print(f"MSE Skoru: {mse}")
                        print(f"MAE Skoru: {mae}")
                        print(f"RMSE Skoru: {rmse}")
                        print(f"MAPE Skoru: {mape}")
                        print(f"sMAPE Skoru: {smape}")
                        print(f"R^2 Skoru: {r2}")

                        # Sonuç sözlüğü oluşturuluyor
                        result_dict = {
                            "Ticker": ticker,
                            "Model": name,
                            "Train_Score": train_score,
                            "Test_Score": test_score,
                            "MSE": mse,
                            "MAE": mae,
                            "RMSE": rmse,
                            "MAPE": mape,
                            "sMAPE": smape,
                            "R2": r2
                        }

                        print("Walk-forward Validation (Pre-trained Model) Sonuçları:")
                        for horizon_name, n_test in horizons.items():
                            # Walk-forward validation fonksiyonu, pre-trained model, scaler ve PLS nesnesini kullanıyor.
                            wf_rmse, wf_mape, wf_smape = walk_forward_validation_pretrained(
                                df, reg, scaler, pls, n_test
                            )
                            print(f"{horizon_name} Walk-forward Validation - RMSE: {wf_rmse}, MAPE: {wf_mape}, sMAPE: {wf_smape}")
                            result_dict[f"WF_RMSE_{horizon_name}"] = wf_rmse
                            result_dict[f"WF_MAPE_{horizon_name}"] = wf_mape
                            result_dict[f"WF_sMAPE_{horizon_name}"] = wf_smape

                        results.append(result_dict)

                    except Exception as e:
                        print(f"{name} modeli {ticker} için hata verdi: {e}")

            except Exception as e:
                print(f"{ticker} için bir hata oluştu: {e}")

        else:
            print(f"\nTicker {ticker} not found in dataframes_dev, skipping...")

    results_df = pd.DataFrame(results)
    return results_df


In [ ]:
evaluate_models_dev_wf_3(["BAX"])


=== BAX için Model Performansı Sonuçları ===

Model: DecisionTree
Train Setindeki Doğruluk: 1.0
Test Setindeki Doğruluk: 0.6196767528557521
MSE Skoru: 4.196225592492696
MAE Skoru: 1.6743219640870757
RMSE Skoru: 2.048469085071263
MAPE Skoru: 4.7332589994946375
sMAPE Skoru: 4.597035538126327
R^2 Skoru: 0.6196767528557521
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 1.2183887822195347, MAPE: 2.6650331236081146, sMAPE: 2.6004267532283976
1 ay Walk-forward Validation - RMSE: 2.057231105772188, MAPE: 5.7341379373771195, sMAPE: 5.509322736506025
3 ay Walk-forward Validation - RMSE: 2.4202971608576256, MAPE: 6.714828549402414, sMAPE: 6.434078659824005
6 ay Walk-forward Validation - RMSE: 2.4744179349444932, MAPE: 6.1373094129504135, sMAPE: 5.887337336996476
1 yıl Walk-forward Validation - RMSE: 2.0219174630400385, MAPE: 4.615246456708448, sMAPE: 4.476957987037313

Model: RandomForest
Train Setindeki Doğruluk: 0.9996523066002121
Test Setindeki 

Ticker             Model  Train_Score  Test_Score         MSE       MAE  \
0     BAX      DecisionTree     1.000000    0.619677    4.196226  1.674322   
1     BAX      RandomForest     0.999652    0.601797    4.393494  1.756014   
2     BAX  GradientBoosting     0.999145    0.731949    2.957488  1.543264   
3     BAX          AdaBoost     0.990547    0.652945    3.829166  1.651347   
4     BAX               KNN     0.996804    0.240950    8.374835  2.465867   
5     BAX  LinearRegression     0.998310    0.973388    0.293615  0.430149   
6     BAX   LassoRegression     0.991977    0.472839    5.816338  2.219179   
7     BAX   RidgeRegression     0.998310    0.973531    0.292042  0.428917   
8     BAX         LinearSVR     0.998241    0.979038    0.231285  0.382028   
9     BAX            RbfSVR     0.986448   -6.867948   86.809537  8.813831   
10    BAX     PolynomialSVR     0.952427  -12.540869  149.400648  9.878089   
11    BAX           XGBoost     0.999995    0.739008    2.879607  1.503417   

         RMSE       MAPE      sMAPE         R2  ...  WF_sMAPE_1 ay  \
0    2.048469   4.733259   4.597036   0.619677  ...       5.509323   
1    2.096066   4.976538   4.810458   0.601797  ...       6.316690   
2    1.719735   4.345278   4.232522   0.731949  ...       6.729447   
3    1.956825   4.683746   4.545419   0.652945  ...       5.346233   
4    2.893931   7.061082   6.742284   0.240950  ...       8.596926   
5    0.541862   1.217605   1.218954   0.973388  ...       1.260779   
6    2.411708   6.216826   5.994979   0.472839  ...       7.372149   
7    0.540409   1.213888   1.215063   0.973531  ...       1.263086   
8    0.480921   1.079097   1.079277   0.979038  ...       1.152751   
9    9.317164  24.874037  21.812798  -6.867948  ...      32.355633   
10  12.222956  28.747039  38.665112 -12.540869  ...     112.161630   
11   1.696941   4.223115   4.112981   0.739008  ...       6.501821   

    WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  \
0       2.420297      6.714829       6.434079      2.474418      6.137309   
1       2.552366      7.266231       6.958488      2.702833      7.291015   
2       2.196041      6.592005       6.357139      1.990892      5.526596   
3       2.765224      7.961845       7.597534      2.286330      5.997470   
4       4.221541     12.532924      11.702711      3.652220      9.892898   
5       0.518907      1.342991       1.352295      0.542897      1.280620   
6       3.099801      9.435972       8.997156      2.815316      7.996068   
7       0.515108      1.335001       1.344020      0.540606      1.274934   
8       0.424853      1.118495       1.124485      0.474941      1.121560   
9      11.859074     37.055209      31.194969     11.513178     33.399020   
10     21.333048     66.656308     102.769817     17.378707     49.135362   
11      2.176566      6.261594       6.031758      1.989896      5.377485   

    WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
0        5.887337       2.021917       4.615246        4.476958  
1        6.994379       2.194390       5.272576        5.087984  
2        5.353778       1.720396       4.363313        4.249844  
3        5.765263       2.106065       5.202822        5.034275  
4        9.328311       2.982219       7.388906        7.038407  
5        1.284778       0.507294       1.155399        1.160158  
6        7.667247       2.588850       6.872309        6.616201  
7        1.278842       0.505359       1.150661        1.155226  
8        1.123336       0.451275       1.024148        1.026916  
9       28.499279       9.583306      25.693360       22.423327  
10      70.487750      13.280147      32.611083       44.391486  
11       5.205760       1.713226       4.258147        4.144640  

[12 rows x 25 columns]

In [ ]:
len(tickers_inf)

503

## [:51]

In [ ]:
globa_0_51 = evaluate_models_dev_wf_3(tickers_inf[:51])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 5.851910514494205, MAPE: 5.74850003630271, sMAPE: 5.926393884681215
1 ay Walk-forward Validation - RMSE: 4.246698803122602, MAPE: 4.2302061610865795, sMAPE: 4.3293016870661925
3 ay Walk-forward Validation - RMSE: 4.733908325502046, MAPE: 4.835654657311515, sMAPE: 4.961432791421889
6 ay Walk-forward Validation - RMSE: 4.883612220645624, MAPE: 4.6644514554532694, sMAPE: 4.7918871959526905
1 yıl Walk-forward Validation - RMSE: 3.490637207752524, MAPE: 2.6894356638407935, sMAPE: 2.7543809054237034

Model: AdaBoost
Train Setindeki Doğruluk: 0.9639022511692731
Test Setindeki Doğruluk: 0.7459087600600528
MSE Skoru: 19.398976166617526
MAE Skoru: 3.32533096537397
RMSE Skoru: 4.404426882877899
MAPE Skoru: 3.5326328061668364
sMAPE Skoru: 3.6338790668639107
R^2 Skoru: 0.7459087600600528
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forw

In [ ]:
globa_0_51["Ticker"].nunique()

51

In [ ]:
globa_0_51.to_excel("global_0_51.xlsx", index=False)

## [51:101]

In [ ]:
globa_51_101 = evaluate_models_dev_wf_3(tickers_inf[51:101])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 1.3421239689325928, MAPE: 1.5182483795962345, sMAPE: 1.5093729978801946
1 ay Walk-forward Validation - RMSE: 1.7096869201413183, MAPE: 1.839108223469465, sMAPE: 1.8173785506772093
3 ay Walk-forward Validation - RMSE: 1.4393089912375103, MAPE: 1.4846980216818322, sMAPE: 1.4732682322265436
6 ay Walk-forward Validation - RMSE: 1.676596619548138, MAPE: 1.5851410497488339, sMAPE: 1.5880064416728716
1 yıl Walk-forward Validation - RMSE: 1.5716520029830405, MAPE: 1.3415452549361135, sMAPE: 1.3451691684146367

Model: AdaBoost
Train Setindeki Doğruluk: 0.9864761335141016
Test Setindeki Doğruluk: 0.8713760093489982
MSE Skoru: 10.274280617448284
MAE Skoru: 2.6382664734418615
RMSE Skoru: 3.2053518710819073
MAPE Skoru: 2.8062125220227996
sMAPE Skoru: 2.807044934139418
R^2 Skoru: 0.8713760093489982
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta

In [ ]:
globa_51_101["Ticker"].nunique()

50

In [ ]:
globa_51_101.to_excel("global_51_101.xlsx", index=False)

## [101:151]

In [ ]:
globa_101_151 = evaluate_models_dev_wf_3(tickers_inf[101:151])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 1.715068912933693, MAPE: 2.327241093196044, sMAPE: 2.3620458436636023
1 ay Walk-forward Validation - RMSE: 1.2421092884808944, MAPE: 1.805140288505578, sMAPE: 1.8245217730004704
3 ay Walk-forward Validation - RMSE: 0.9135499561559876, MAPE: 1.2283979539536487, sMAPE: 1.237270446718921
6 ay Walk-forward Validation - RMSE: 1.0160443214534427, MAPE: 1.4162736268253489, sMAPE: 1.428267253878999
1 yıl Walk-forward Validation - RMSE: 1.1806826443901326, MAPE: 1.6533382765955906, sMAPE: 1.6712364013302365

Model: AdaBoost
Train Setindeki Doğruluk: 0.9834976619896902
Test Setindeki Doğruluk: 0.7174866087239054
MSE Skoru: 2.9833648796649217
MAE Skoru: 1.3978863533075498
RMSE Skoru: 1.7272419864237094
MAPE Skoru: 2.444251068204565
sMAPE Skoru: 2.4866593647236432
R^2 Skoru: 0.7174866087239054
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Wa

In [ ]:
globa_101_151["Ticker"].nunique()

50

In [ ]:
globa_101_151.to_excel("global_101_151.xlsx", index =False)

## [151:201]

In [ ]:
globa_151_201 = evaluate_models_dev_wf_3(tickers_inf[151:201])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 2.040585787933207, MAPE: 0.6584309811080274, sMAPE: 0.6563218368066165
1 ay Walk-forward Validation - RMSE: 1.8298465678070888, MAPE: 0.5015149013441652, sMAPE: 0.5000733124974449
3 ay Walk-forward Validation - RMSE: 2.9944004659187797, MAPE: 0.7497184325058002, sMAPE: 0.7516397668333819
6 ay Walk-forward Validation - RMSE: 3.215791645783897, MAPE: 0.7923250364565638, sMAPE: 0.7958990390733741
1 yıl Walk-forward Validation - RMSE: 3.1976556567433057, MAPE: 0.9232037735691433, sMAPE: 0.9289214034637682

Model: AdaBoost
Train Setindeki Doğruluk: 0.9794596832585476
Test Setindeki Doğruluk: 0.9433593512067308
MSE Skoru: 49.773067707124106
MAE Skoru: 5.900597834581001
RMSE Skoru: 7.055003026726785
MAPE Skoru: 2.26866689780574
sMAPE Skoru: 2.291100663992559
R^2 Skoru: 0.9433593512067308
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Wal

In [ ]:
globa_151_201["Ticker"].nunique()

50

In [ ]:
globa_151_201.to_excel("global_151_201.xlsx", index =False)

## [201:251]

In [ ]:
globa_201_251 = evaluate_models_dev_wf_3(tickers_inf[201:251])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 1.5564590206940372, MAPE: 1.6857892217984778, sMAPE: 1.7044672146813704
1 ay Walk-forward Validation - RMSE: 1.1538455085364432, MAPE: 1.2991677044777998, sMAPE: 1.3061673862904315
3 ay Walk-forward Validation - RMSE: 1.0977055361479586, MAPE: 1.1153677843615044, sMAPE: 1.1172349377010347
6 ay Walk-forward Validation - RMSE: 1.0265544658006311, MAPE: 1.091706717325579, sMAPE: 1.0965029886585165
1 yıl Walk-forward Validation - RMSE: 1.0157067772367185, MAPE: 1.099842784423468, sMAPE: 1.101943373933113

Model: AdaBoost
Train Setindeki Doğruluk: 0.9743771656554739
Test Setindeki Doğruluk: 0.890257046275328
MSE Skoru: 1.1729748420847328
MAE Skoru: 0.8650970795880765
RMSE Skoru: 1.083039630892948
MAPE Skoru: 1.207219526484538
sMAPE Skoru: 1.2109661939862735
R^2 Skoru: 0.890257046275328
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Wal

In [ ]:
globa_201_251["Ticker"].nunique()

49

In [ ]:
globa_201_251.to_excel("global_201_251.xlsx", index =False)

## [251:301]

In [ ]:
globa_251_301 = evaluate_models_dev_wf_3(tickers_inf[251:301])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 87.81688068623407, MAPE: 52.977790600707195, sMAPE: 72.07115008923827
1 ay Walk-forward Validation - RMSE: 79.18381461686539, MAPE: 50.67205088221092, sMAPE: 67.90328818002371
3 ay Walk-forward Validation - RMSE: 76.56732980228583, MAPE: 49.75516005516266, sMAPE: 66.28375327956297
6 ay Walk-forward Validation - RMSE: 64.67639615512503, MAPE: 44.326314687011894, sMAPE: 57.356070024760186
1 yıl Walk-forward Validation - RMSE: 49.40265881917556, MAPE: 34.5125820736765, sMAPE: 42.86396992565719

Model: AdaBoost
Train Setindeki Doğruluk: 0.9848962609518268
Test Setindeki Doğruluk: -2.3450530954327653
MSE Skoru: 2270.12427710524
MAE Skoru: 40.14681880741108
RMSE Skoru: 47.64582119247437
MAPE Skoru: 31.987950860665748
sMAPE Skoru: 39.96597682264428
R^2 Skoru: -2.3450530954327653
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward

In [ ]:
globa_251_301["Ticker"].nunique()

50

In [ ]:
globa_251_301.to_excel("global_251_301.xlsx", index =False)

## [301:351]

In [ ]:
globa_301_351 = evaluate_models_dev_wf_3(tickers_inf[301:351])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 107.74560321358408, MAPE: 21.733851965094896, sMAPE: 24.38412514643766
1 ay Walk-forward Validation - RMSE: 97.25464057877137, MAPE: 20.22899433249282, sMAPE: 22.512877255036237
3 ay Walk-forward Validation - RMSE: 95.97771712334442, MAPE: 19.87811874046785, sMAPE: 22.08996432526112
6 ay Walk-forward Validation - RMSE: 91.80532623853593, MAPE: 19.094324658562922, sMAPE: 21.134764780505037
1 yıl Walk-forward Validation - RMSE: 67.31666377270112, MAPE: 11.675519447066662, sMAPE: 12.784709103220182

Model: AdaBoost
Train Setindeki Doğruluk: 0.9810748548296405
Test Setindeki Doğruluk: -1.478131096278176
MSE Skoru: 5110.17094051373
MAE Skoru: 57.50985021020589
RMSE Skoru: 71.48545964399844
MAPE Skoru: 12.550309133800624
sMAPE Skoru: 13.834202745968577
R^2 Skoru: -1.478131096278176
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-for

In [ ]:
globa_301_351["Ticker"].nunique()

50

In [ ]:
globa_301_351.to_excel("global_301_351.xlsx", index =False)

## [351:401]

In [ ]:
globa_351_401 = evaluate_models_dev_wf_3(tickers_inf[351:401])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 2.2737137649303314, MAPE: 1.4906031908471469, sMAPE: 1.5088487665601136
1 ay Walk-forward Validation - RMSE: 3.455476777540861, MAPE: 2.5228804662949753, sMAPE: 2.567671820801243
3 ay Walk-forward Validation - RMSE: 2.2943032285516023, MAPE: 1.4052153826291274, sMAPE: 1.4194475613149253
6 ay Walk-forward Validation - RMSE: 2.038202174289431, MAPE: 1.2631397850710668, sMAPE: 1.2684208289581815
1 yıl Walk-forward Validation - RMSE: 1.9208500174084748, MAPE: 1.1983083717545715, sMAPE: 1.2048979813817646

Model: AdaBoost
Train Setindeki Doğruluk: 0.980539215561733
Test Setindeki Doğruluk: 0.8748781018030615
MSE Skoru: 7.688222309111531
MAE Skoru: 2.268792452215441
RMSE Skoru: 2.7727643803813424
MAPE Skoru: 1.7395059534622577
sMAPE Skoru: 1.753851291976452
R^2 Skoru: 0.8748781018030615
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Wal

In [ ]:
globa_351_401["Ticker"].nunique()

50

In [ ]:
globa_351_401.to_excel("global_351_401.xlsx", index =False)

## [401:451]

In [ ]:
globa_401_451 = evaluate_models_dev_wf_3(tickers_inf[401:451])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 93.78965913344791, MAPE: 23.824411647114545, sMAPE: 27.046809304797343
1 ay Walk-forward Validation - RMSE: 85.29047475757332, MAPE: 22.44459688652331, sMAPE: 25.29383009394136
3 ay Walk-forward Validation - RMSE: 84.56432853648533, MAPE: 22.317350573950275, sMAPE: 25.135208262223784
6 ay Walk-forward Validation - RMSE: 73.94110454448571, MAPE: 19.741230016537145, sMAPE: 21.97397368156026
1 yıl Walk-forward Validation - RMSE: 61.610907948955735, MAPE: 16.602271137280532, sMAPE: 18.21221352614178

Model: AdaBoost
Train Setindeki Doğruluk: 0.9801226867801085
Test Setindeki Doğruluk: -4.749751152736518
MSE Skoru: 4246.750294706999
MAE Skoru: 59.382288540828135
RMSE Skoru: 65.1670951838963
MAPE Skoru: 16.80364888820459
sMAPE Skoru: 18.639160493461517
R^2 Skoru: -4.749751152736518
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-for

In [ ]:
globa_401_451["Ticker"].nunique()

48

In [ ]:
globa_401_451.to_excel("global_401_451.xlsx", index =False)

## [451:503]

In [ ]:
globa_451_end = evaluate_models_dev_wf_3(tickers_inf[451:len(tickers_inf)])

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-forward Validation - RMSE: 344.399195305412, MAPE: 30.92364040969352, sMAPE: 36.580616900396386
1 ay Walk-forward Validation - RMSE: 333.82968377129924, MAPE: 30.536045659916017, sMAPE: 36.042320051377416
3 ay Walk-forward Validation - RMSE: 376.36395737571917, MAPE: 32.8523713960321, sMAPE: 39.367727242745396
6 ay Walk-forward Validation - RMSE: 313.7416648099718, MAPE: 27.681137105587506, sMAPE: 32.41405498751962
1 yıl Walk-forward Validation - RMSE: 259.37517815663347, MAPE: 23.68748718590582, sMAPE: 27.15843360097441

Model: AdaBoost
Train Setindeki Doğruluk: 0.992191447092363
Test Setindeki Doğruluk: -4.211476242695034
MSE Skoru: 60534.03164410966
MAE Skoru: 221.78762791156137
RMSE Skoru: 246.03664695347655
MAPE Skoru: 21.758960779426832
sMAPE Skoru: 24.91859659080373
R^2 Skoru: -4.211476242695034
Walk-forward Validation (Pre-trained Model) Sonuçları:
1 hafta Walk-for

In [ ]:
globa_451_end["Ticker"].nunique()

52

In [ ]:
globa_451_end.to_excel("global_401_end.xlsx", index =False)

## Kontrol ve Eksikliklerin Giderilmesi (Birleşitirilmiş: `global_results`)

In [ ]:
global_results = pd.concat([globa_0_51, globa_51_101, globa_101_151, globa_151_201, globa_201_251, globa_251_301, globa_301_351, globa_351_401, globa_401_451, globa_451_end], ignore_index=True)

In [ ]:
global_results

Ticker             Model  Train_Score  Test_Score          MSE  \
0       MMM      DecisionTree     1.000000    0.966817    17.271589   
1       MMM      RandomForest     0.999554    0.973585    13.748970   
2       MMM  GradientBoosting     0.998642    0.985981     7.297035   
3       MMM          AdaBoost     0.988160    0.954708    23.574354   
4       MMM               KNN     0.995524    0.900356    51.864609   
...     ...               ...          ...         ...          ...   
5995   BF-B   RidgeRegression     0.995769    0.994819     0.212696   
5996   BF-B         LinearSVR     0.995654    0.995714     0.175949   
5997   BF-B            RbfSVR     0.982499   -1.383991    97.875919   
5998   BF-B     PolynomialSVR     0.950353  -27.910213  1186.923211   
5999   BF-B           XGBoost     0.999989    0.670975    13.508287   

            MAE       RMSE       MAPE      sMAPE         R2  ...  \
0      3.310258   4.155910   3.056547   3.109222   0.966817  ...   
1      2.868003   3.707960   2.620947   2.670566   0.973585  ...   
2      2.013338   2.701302   1.844672   1.870785   0.985981  ...   
3      3.891283   4.855343   3.565052   3.654805   0.954708  ...   
4      5.880322   7.201709   5.173306   5.181401   0.900356  ...   
...         ...        ...        ...        ...        ...  ...   
5995   0.365162   0.461189   0.802207   0.806093   0.994819  ...   
5996   0.320546   0.419463   0.697079   0.699782   0.995714  ...   
5997   6.979945   9.893226  17.009139  14.348250  -1.383991  ...   
5998  20.492523  34.451752  51.392855  59.426756 -27.910213  ...   
5999   2.841226   3.675362   6.658257   6.268950   0.670975  ...   

      WF_sMAPE_1 ay  WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  \
0          3.198092      4.301251      2.654842       2.652268      4.704311   
1          2.741951      3.333614      1.858409       1.866871      4.005798   
2          1.957728      2.201425      1.009523       1.019135      2.891855   
3          3.763365      4.058034      1.950482       1.989622      5.537225   
4          5.627663      9.352578      6.669513       6.482589      9.058322   
...             ...           ...           ...            ...           ...   
5995       1.388214      0.608893      1.298119       1.310021      0.507395   
5996       1.042005      0.529288      1.069620       1.077789      0.454405   
5997      53.051361     17.556641     42.557898      33.506623     12.909196   
5998     200.000000     67.129727    147.934419     139.541767     48.269667   
5999      21.849972      5.456762     12.383586      11.296206      4.028582   

      WF_MAPE_6 ay  WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  \
0         2.970513       2.996367       4.414299       3.187377   
1         2.408372       2.443356       3.969860       2.765788   
2         1.666867       1.689001       2.889715       1.928997   
3         3.297630       3.386910       5.154086       3.659847   
4         6.474498       6.290489       7.810724       5.725221   
...            ...            ...            ...            ...   
5995      0.985869       0.993387       0.456823       0.832953   
5996      0.853598       0.859196       0.409373       0.714108   
5997     25.346211      20.530404      10.809708      20.019077   
5998     83.305127      81.733784      37.653928      59.981997   
5999      7.698923       7.122592       3.993577       7.652523   

      WF_sMAPE_1 yıl  
0           3.242024  
1           2.820628  
2           1.958704  
3           3.757428  
4           5.731743  
...              ...  
5995        0.837853  
5996        0.717601  
5997       16.837640  
5998       69.657841  
5999        7.188191  

[6000 rows x 25 columns]

from matplotlib import pyplot as plt
global_results['Train_Score'].plot(kind='hist', bins=20, title='Train_Score')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
global_results['Test_Score'].plot(kind='hist', bins=20, title='Test_Score')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
global_results['MSE'].plot(kind='hist', bins=20, title='MSE')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
global_results['MAE'].plot(kind='hist', bins=20, title='MAE')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
global_results.plot(kind='scatter', x='MAE', y='RMSE', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
global_results['Train_Score'].plot(kind='line', figsize=(8, 4), title='Train_Score')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
global_results['Test_Score'].plot(kind='line', figsize=(8, 4), title='Test_Score')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
global_results['MSE'].plot(kind='line', figsize=(8, 4), title='MSE')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
global_results['MAE'].plot(kind='line', figsize=(8, 4), title='MAE')
plt.gca().spines[['top', 'right']].set_visible(False)

In [ ]:
global_results["Ticker"].nunique()

500

In [ ]:
global_results.to_excel("all_results.xlsx", index=False)

In [ ]:
global_results.describe()

Train_Score     Test_Score           MSE           MAE          RMSE  \
count  6000.000000    6000.000000  6.000000e+03   6000.000000   6000.000000   
mean      0.986154    -140.642983  3.709610e+05     48.346080     63.783286   
std       0.030868    6945.136430  1.324152e+07    391.262594    605.767182   
min       0.228341 -525758.825489  5.147075e-03      0.053834      0.071743   
25%       0.986908      -0.858124  2.602079e+00      1.195988      1.613096   
50%       0.997186       0.796476  2.279715e+01      3.625604      4.774636   
75%       0.998994       0.973246  4.702231e+02     16.978369     21.684628   
max       1.000000       0.999034  8.776074e+08  15723.735297  29624.438513   

               MAPE        sMAPE             R2  WF_RMSE_1 hafta  \
count   6000.000000  6000.000000    6000.000000      6000.000000   
mean      17.825853    10.702140    -140.642983       119.310093   
std      171.407042    18.764762    6945.136430      1846.579372   
min        0.305015     0.304955 -525758.825489         0.018581   
25%        1.169400     1.168512      -0.858124         1.291937   
50%        3.243791     3.264125       0.796476         4.724564   
75%       10.937425    11.523775       0.973246        28.773202   
max    11493.590496   184.221471       0.999034    127618.647377   

       WF_MAPE_1 hafta  ...  WF_sMAPE_1 ay  WF_RMSE_3 ay  WF_MAPE_3 ay  \
count      6000.000000  ...    6000.000000   6000.000000   6000.000000   
mean         47.243316  ...      16.506167    104.005047     35.536657   
std        1084.795550  ...      29.062881   1179.812875    500.962358   
min           0.082175  ...       0.231750      0.077372      0.194066   
25%           1.017445  ...       1.082300      1.676698      1.194463   
50%           3.469099  ...       3.382050      5.317390      3.572011   
75%          19.331954  ...      19.455779     28.276012     17.982286   
max       81543.835015  ...     200.000000  61587.285434  35385.881665   

       WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  WF_sMAPE_6 ay  \
count    6000.000000   6000.000000   6000.000000    6000.000000   
mean       16.454581     88.958039     28.767746      14.765042   
std        28.433703    918.854519    352.244010      25.761546   
min         0.193192      0.070641      0.152899       0.152211   
25%         1.194522      1.683450      1.189807       1.189678   
50%         3.596361      5.251626      3.514989       3.560212   
75%        19.468710     26.081033     16.419383      17.521026   
max       200.000000  45737.006392  24479.631908     200.000000   

       WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
count    6000.000000    6000.000000     6000.000000  
mean       69.201702      20.359212       11.916614  
std       662.606411     204.451326       21.193547  
min         0.072481       0.152899        0.152211  
25%         1.633471       1.161502        1.161827  
50%         4.908657       3.296353        3.326221  
75%        23.136490      12.177088       12.930167  
max     32430.475590   13766.292150      198.378725  

[8 rows x 23 columns]

In [ ]:
global_results[global_results["Ticker"] == "ALB"]

Ticker             Model  Train_Score  Test_Score          MSE        MAE  \
156    ALB      DecisionTree     1.000000   -0.559568   469.207632  19.124138   
157    ALB      RandomForest     0.999410   -0.291463   388.546275  16.998894   
158    ALB  GradientBoosting     0.998481    0.295141   212.062151  12.823388   
159    ALB          AdaBoost     0.987361   -0.915764   576.371867  20.095792   
160    ALB               KNN     0.996895   -1.207834   664.243403  23.101237   
161    ALB  LinearRegression     0.997638    0.975362     7.412529   2.121240   
162    ALB   LassoRegression     0.994542    0.976263     7.141474   2.064297   
163    ALB   RidgeRegression     0.997638    0.975439     7.389381   2.117335   
164    ALB         LinearSVR     0.997533    0.981555     5.549166   1.860282   
165    ALB            RbfSVR     0.969522    0.435694   169.775798  10.321104   
166    ALB     PolynomialSVR     0.939591   -3.398568  1323.341840  35.367668   
167    ALB           XGBoost     0.999993    0.303234   209.627332  11.654452   

          RMSE       MAPE      sMAPE        R2  ...  WF_sMAPE_1 ay  \
156  21.661201  18.712288  16.837948 -0.559568  ...      14.699434   
157  19.711577  16.735284  14.990950 -0.291463  ...       8.627593   
158  14.562354  12.486312  11.522144  0.295141  ...       5.157150   
159  24.007746  19.149719  16.801691 -0.915764  ...       2.821231   
160  25.772920  21.685288  22.270915 -1.207834  ...      18.313970   
161   2.722596   2.074303   2.096445  0.975362  ...       4.309067   
162   2.672354   1.986893   1.998412  0.976263  ...       3.164402   
163   2.718342   2.070097   2.092059  0.975439  ...       4.299675   
164   2.355667   1.785892   1.798376  0.981555  ...       3.458427   
165  13.029804   9.814791   9.274398  0.435694  ...      10.052817   
166  36.377766  34.608783  29.046615 -3.398568  ...      34.248763   
167  14.478513  11.164111  10.350436  0.303234  ...       7.222029   

     WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  \
156     15.208022     14.086741      12.847315     20.873530     21.019917   
157     10.103212      9.182097       8.624828     18.338700     17.635673   
158      7.965787      7.379955       7.048069     13.443165     13.234625   
159      6.850369      5.239192       5.090373     17.315958     14.067788   
160     19.542398     19.441323      21.612353     20.775972     21.630968   
161      3.114374      2.758705       2.806355      2.816154      2.522657   
162      2.495785      2.094711       2.129248      2.456811      2.119478   
163      3.108828      2.753542       2.801046      2.809430      2.515933   
164      2.476435      2.208634       2.235743      2.272658      2.059423   
165      8.136534      7.376282       7.735953     10.881040      9.366490   
166     38.507905     39.856247      33.180356     40.760147     43.915602   
167      6.541808      5.576310       5.351405     10.308891      9.473235   

     WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
156      18.481666      22.273619      20.151275       17.837559  
157      15.608862      20.768877      18.364546       16.358252  
158      12.124593      15.019653      13.341891       12.273442  
159      12.308925      25.264855      20.663840       18.015503  
160      24.597398      26.773491      24.156837       25.018323  
161       2.559791       2.811473       2.226309        2.254583  
162       2.147387       2.630289       2.007136        2.024597  
163       2.552826       2.806578       2.221476        2.249563  
164       2.081922       2.364993       1.864090        1.880637  
165       9.094297      11.860639       9.085865        8.632701  
166      35.889017      38.574870      38.091534       31.712925  
167       8.812050      14.372705      11.609113       10.687052  

[12 rows x 25 columns]

In [ ]:
global_results[global_results["Ticker"] == "VLTO"]

Ticker             Model  Train_Score  Test_Score       MSE       MAE  \
5556   VLTO      DecisionTree     1.000000   -2.956907  3.903537  1.740996   
5557   VLTO      RandomForest     0.992328   -0.600069  1.578487  0.957724   
5558   VLTO  GradientBoosting     0.999949   -0.439766  1.420346  1.075909   
5559   VLTO          AdaBoost     0.986610   -2.264968  3.220930  1.499805   
5560   VLTO               KNN     0.977476    0.018832  0.967934  0.844170   
5561   VLTO  LinearRegression     0.996802   -4.538504  5.463801  2.006372   
5562   VLTO   LassoRegression     0.943565    0.407332  0.584674  0.652879   
5563   VLTO   RidgeRegression     0.996767   -3.461346  4.401172  1.779094   
5564   VLTO         LinearSVR     0.996723   -4.092892  5.024199  1.926633   
5565   VLTO            RbfSVR     0.982123   -5.232011  6.147953  2.285044   
5566   VLTO     PolynomialSVR     0.947835   -0.413689  1.394621  0.969974   
5567   VLTO           XGBoost     1.000000   -0.215583  1.199187  0.783387   

          RMSE      MAPE     sMAPE        R2  ...  WF_sMAPE_1 ay  \
5556  1.975737  1.690878  1.701712 -2.956907  ...       1.296543   
5557  1.256379  0.931878  0.927028 -0.600069  ...       0.752688   
5558  1.191783  1.046339  1.042652 -0.439766  ...       0.798105   
5559  1.794695  1.456973  1.445112 -2.264968  ...       1.201014   
5560  0.983836  0.820751  0.823640  0.018832  ...       0.708252   
5561  2.337477  1.947061  1.973148 -4.538504  ...       1.532324   
5562  0.764640  0.636461  0.637328  0.407332  ...       0.694374   
5563  2.097897  1.726192  1.747174 -3.461346  ...       1.358499   
5564  2.241472  1.869625  1.893596 -4.092892  ...       1.470311   
5565  2.479507  2.226839  2.198033 -5.232011  ...       1.833598   
5566  1.180941  0.947637  0.953510 -0.413689  ...       0.771670   
5567  1.095074  0.762811  0.759368 -0.215583  ...       0.578679   

      WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  \
5556      0.995678      0.429429       0.432181      0.883576      0.338176   
5557      0.683020      0.406108       0.404938      0.635833      0.381950   
5558      0.601127      0.283010       0.282074      0.533536      0.225839   
5559      0.993152      0.658304       0.655399      0.893752      0.565349   
5560      0.692253      0.533888       0.534567      0.673546      0.509166   
5561      1.193189      0.623044       0.629663      1.062865      0.519758   
5562      0.851733      0.683918       0.683477      0.876683      0.704801   
5563      1.074121      0.568017       0.573337      0.957896      0.476450   
5564      1.146166      0.606156       0.612245      1.021119      0.504904   
5565      1.305486      0.787286       0.779535      1.198335      0.714047   
5566      1.049070      0.766927       0.768936      0.938753      0.642568   
5567      0.551866      0.194066       0.193192      0.489732      0.152899   

      WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
5556       0.340342       0.883576       0.338176        0.340342  
5557       0.380937       0.635833       0.381950        0.380937  
5558       0.225102       0.533536       0.225839        0.225102  
5559       0.563013       0.893752       0.565349        0.563013  
5560       0.509558       0.673546       0.509166        0.509558  
5561       0.524957       1.062865       0.519758        0.524957  
5562       0.704693       0.876683       0.704801        0.704693  
5563       0.480628       0.957896       0.476450        0.480628  
5564       0.509682       1.021119       0.504904        0.509682  
5565       0.708287       1.198335       0.714047        0.708287  
5566       0.644163       0.938753       0.642568        0.644163  
5567       0.152211       0.489732       0.152899        0.152211  

[12 rows x 25 columns]

In [ ]:
global_results[global_results["Ticker"] == "EA"]

Ticker             Model  Train_Score  Test_Score         MSE        MAE  \
1956     EA      DecisionTree     1.000000    0.450890   56.148129   4.515983   
1957     EA      RandomForest     0.999126    0.467705   54.428794   4.390783   
1958     EA  GradientBoosting     0.997346    0.435009   57.772058   4.680087   
1959     EA          AdaBoost     0.983054    0.230400   78.693951   5.758649   
1960     EA               KNN     0.994276    0.417450   59.567519   5.259863   
1961     EA  LinearRegression     0.996000    0.984707    1.563711   0.850684   
1962     EA   LassoRegression     0.984029    0.936231    6.520552   1.537662   
1963     EA   RidgeRegression     0.996000    0.984687    1.565768   0.850597   
1964     EA         LinearSVR     0.995883    0.985504    1.482234   0.800747   
1965     EA            RbfSVR     0.980128   -0.766666  180.646954   7.921496   
1966     EA     PolynomialSVR     0.960819   -2.955400  404.451528  10.491179   
1967     EA           XGBoost     0.999980    0.417080   59.605356   4.687512   

           RMSE      MAPE     sMAPE        R2  ...  WF_sMAPE_1 ay  \
1956   7.493206  3.090470  3.146833  0.450890  ...       6.274324   
1957   7.377587  2.958568  3.039123  0.467705  ...       7.591540   
1958   7.600793  3.136604  3.242044  0.435009  ...       7.321380   
1959   8.870961  3.875858  4.016297  0.230400  ...       8.526237   
1960   7.718000  3.556424  3.668165  0.417450  ...       7.125189   
1961   1.250484  0.622104  0.620023  0.984707  ...       1.814657   
1962   2.553537  1.117149  1.105189  0.936231  ...       4.469309   
1963   1.251306  0.622074  0.619985  0.984687  ...       1.817524   
1964   1.217470  0.584188  0.581802  0.985504  ...       1.704146   
1965  13.440497  5.219316  5.616332 -0.766666  ...       9.421702   
1966  20.110980  6.959739  6.431321 -2.955400  ...      14.344052   
1967   7.720450  3.140901  3.251068  0.417080  ...       7.565619   

      WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  \
1956     15.481515      8.754837       8.981286     11.205145      5.341258   
1957     15.533564      9.482082       9.834094     11.273093      5.801951   
1958     15.782816      9.646839      10.092411     11.635243      6.360938   
1959     17.942390     10.979269      11.529096     13.486174      7.635868   
1960     15.595312      9.328224       9.820002     11.560117      6.296990   
1961      2.106341      0.966519       0.954719      1.564397      0.680986   
1962      5.020996      2.563055       2.498102      3.597396      1.507356   
1963      2.109531      0.967747       0.955903      1.566462      0.681471   
1964      2.132900      0.987629       0.975056      1.569757      0.674202   
1965     28.070411     16.034899      17.756937     20.541760     10.494672   
1966     43.340874     24.238448      21.632116     30.755670     13.216751   
1967     16.194818      9.782139      10.268916     11.779681      6.099926   

      WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
1956       5.467511       8.159224       3.477848        3.545570  
1957       5.993026       8.059921       3.397489        3.494404  
1958       6.609521       8.297415       3.600111        3.726662  
1959       7.960904       9.691511       4.476371        4.644765  
1960       6.571718       8.384377       3.971314        4.107868  
1961       0.675335       1.278944       0.620793        0.618579  
1962       1.475054       2.751720       1.213816        1.199052  
1963       0.675798       1.279943       0.620813        0.618590  
1964       0.668075       1.255528       0.587808        0.585217  
1965      11.423590      14.691909       6.030774        6.506511  
1966      11.899141      21.845874       7.507534        6.856032  
1967       6.361279       8.421930       3.570501        3.703087  

[12 rows x 25 columns]

In [ ]:
global_results[global_results["Ticker"] == "EG"]

Ticker             Model  Train_Score  Test_Score          MSE  \
2124     EG      DecisionTree     1.000000    0.470735    95.242242   
2125     EG      RandomForest     0.999607    0.683284    56.993734   
2126     EG  GradientBoosting     0.998912    0.873527    22.759085   
2127     EG          AdaBoost     0.986382    0.702971    53.451019   
2128     EG               KNN     0.997344    0.327293   121.054882   
2129     EG  LinearRegression     0.998000    0.944030    10.071893   
2130     EG   LassoRegression     0.993220    0.741027    46.602742   
2131     EG   RidgeRegression     0.998000    0.943916    10.092513   
2132     EG         LinearSVR     0.997865    0.919727    14.445279   
2133     EG            RbfSVR     0.933872  -26.716062  4987.559227   
2134     EG     PolynomialSVR     0.885634   -6.820893  1407.384982   
2135     EG           XGBoost     0.999993    0.826867    31.155545   

            MAE       RMSE       MAPE      sMAPE         R2  ...  \
2124   7.767467   9.759213   2.111420   2.093447   0.470735  ...   
2125   5.403075   7.549419   1.471502   1.452902   0.683284  ...   
2126   3.581991   4.770648   0.965241   0.960552   0.873527  ...   
2127   5.629602   7.311020   1.507240   1.507721   0.702971  ...   
2128   9.211878  11.002494   2.484249   2.463987   0.327293  ...   
2129   2.195829   3.173625   0.594696   0.591717   0.944030  ...   
2130   5.645656   6.826620   1.532540   1.515310   0.741027  ...   
2131   2.197586   3.176872   0.595194   0.592204   0.943916  ...   
2132   2.578357   3.800695   0.700538   0.695598   0.919727  ...   
2133  69.261105  70.622654  18.471648  20.427006 -26.716062  ...   
2134  30.549181  37.515130   8.109482   7.655501  -6.820893  ...   
2135   4.241337   5.581715   1.132628   1.136059   0.826867  ...   

      WF_sMAPE_1 ay  WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  \
2124       2.161581     10.886526      2.517753       2.491822      9.822688   
2125       1.451205      9.017635      1.927863       1.899494      8.227642   
2126       1.088800      5.161220      1.130553       1.123564      5.190207   
2127       1.093190      8.054251      1.713997       1.704908      7.769985   
2128       4.236308     14.328491      3.552763       3.483546     12.594294   
2129       0.794052      3.403144      0.672351       0.669046      3.505635   
2130       1.670482      8.284204      1.974239       1.948248      7.686547   
2131       0.794390      3.409099      0.673376       0.670049      3.510349   
2132       0.858231      4.125229      0.803976       0.798066      4.194804   
2133      20.046711     74.741795     20.178402      22.482976     79.915673   
2134       4.673664     22.625029      5.537438       5.360575     34.636547   
2135       1.187744      6.242130      1.351444       1.350191      6.144476   

      WF_MAPE_6 ay  WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  \
2124      2.181737       2.159007       9.062727       1.989918   
2125      1.705670       1.683187       6.667459       1.304633   
2126      1.134301       1.128673       4.240554       0.873442   
2127      1.603991       1.598823       6.619614       1.381045   
2128      2.985970       2.955673      10.937659       2.469784   
2129      0.675131       0.671364       2.939088       0.563386   
2130      1.745256       1.723337       6.515442       1.470656   
2131      0.675930       0.672146       2.942189       0.563808   
2132      0.792610       0.786459       3.541652       0.666669   
2133     21.043632      23.573399      72.488740      18.991941   
2134      7.798100       7.413658      31.037337       6.645355   
2135      1.248901       1.251349       5.203520       1.058964   

      WF_sMAPE_1 yıl  
2124        1.979838  
2125        1.290170  
2126        0.869840  
2127        1.381894  
2128        2.445201  
2129        0.560912  
2130        1.455034  
2131        0.561323  
2132        0.662405  
2133       21.055827  
2134        6.335722  
2135   

In [ ]:
global_results[global_results["Ticker"] == "MTCH"]

Ticker             Model  Train_Score  Test_Score         MSE        MAE  \
3636   MTCH      DecisionTree     1.000000    0.022373    6.163584   2.134101   
3637   MTCH      RandomForest     0.999560    0.174878    5.202095   1.977705   
3638   MTCH  GradientBoosting     0.998490   -2.829069   24.140882   4.629515   
3639   MTCH          AdaBoost     0.987434   -4.570900   35.122493   5.368227   
3640   MTCH               KNN     0.997191   -8.058822   57.112568   7.035937   
3641   MTCH  LinearRegression     0.997883    0.507326    3.106130   1.461505   
3642   MTCH   LassoRegression     0.991817   -0.271372    8.015539   2.291695   
3643   MTCH   RidgeRegression     0.997883    0.508706    3.097427   1.459640   
3644   MTCH         LinearSVR     0.997843    0.575837    2.674193   1.357882   
3645   MTCH            RbfSVR     0.979096  -14.765903   99.398270   9.443007   
3646   MTCH     PolynomialSVR     0.948095  -54.702326  351.182852  17.624416   
3647   MTCH           XGBoost     0.999995   -2.151907   19.871627   4.025914   

           RMSE       MAPE      sMAPE         R2  ...  WF_sMAPE_1 ay  \
3636   2.482657   6.452746   6.318401   0.022373  ...       4.852953   
3637   2.280810   5.980598   5.862167   0.174878  ...       4.445130   
3638   4.913337  13.892929  12.867503  -2.829069  ...      16.485867   
3639   5.926423  16.480466  14.928849  -4.570900  ...      17.073521   
3640   7.557286  20.905211  18.651434  -8.058822  ...      24.679949   
3641   1.762422   4.309391   4.257427   0.507326  ...       4.979683   
3642   2.831173   6.892039   7.225305  -0.271372  ...       4.271582   
3643   1.759951   4.303874   4.252191   0.508706  ...       4.973510   
3644   1.635296   4.008364   3.967635   0.575837  ...       4.645265   
3645   9.969868  28.022059  24.281859 -14.765903  ...      23.714665   
3646  18.739873  52.169632  75.052260 -54.702326  ...      75.167940   
3647   4.457760  12.171794  11.307946  -2.151907  ...      12.049808   

      WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  \
3636      2.366592      6.627088       6.385749      2.334397      6.033176   
3637      2.124856      5.929432       5.722955      1.999647      5.285389   
3638      5.794021     17.432605      15.986129      5.087421     14.505040   
3639      6.809136     20.457398      18.410635      5.265486     14.140953   
3640      8.938589     26.795392      23.517818      8.514301     24.435293   
3641      1.701071      4.276799       4.233184      1.662329      3.893653   
3642      1.681880      4.085195       4.122214      1.830048      4.195250   
3643      1.698905      4.270493       4.226578      1.661327      3.891563   
3644      1.594644      4.017925       3.978274      1.538299      3.609171   
3645     10.561764     30.371294      26.005449     10.262081     28.548185   
3646     17.013791     50.529521      69.235197     20.398242     57.160474   
3647      4.739310     14.094515      13.103349      4.234919     11.725406   

      WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
3636       6.010702       2.557972       6.707648        6.539293  
3637       5.247150       2.364680       6.296738        6.142108  
3638      13.457827       5.205605      15.075022       13.917233  
3639      12.947108       6.076512      17.030613       15.389065  
3640      21.685664       8.118503      23.431321       20.819672  
3641       3.836261       1.620933       3.983389        3.962647  
3642       4.185462       2.841566       6.871387        7.201978  
3643       3.833927       1.619811       3.980568        3.959894  
3644       3.560932       1.508633       3.715938        3.702438  
3645      24.747731      10.408597      29.681120       25.581332  
3646      81.737520      20.143379      58.299917       85.015878  
3647      10.990529       4.737554      13.448218       12.463101  

[12 rows x 25 columns]

In [ ]:
global_results[global_results["Ticker"] == "WBD"]

Ticker             Model  Train_Score  Test_Score         MSE        MAE  \
5748    WBD      DecisionTree     1.000000   -0.492836    2.920931   1.387351   
5749    WBD      RandomForest     0.998798   -0.356555    2.654281   1.319692   
5750    WBD  GradientBoosting     0.997936   -1.229391    4.362100   1.766062   
5751    WBD          AdaBoost     0.978654   -6.115168   13.921770   3.462822   
5752    WBD               KNN     0.995902   -2.683624    7.207500   2.461828   
5753    WBD  LinearRegression     0.997222    0.951863    0.094186   0.249204   
5754    WBD   LassoRegression     0.968889   -0.615047    3.160053   1.373982   
5755    WBD   RidgeRegression     0.997222    0.951521    0.094856   0.250133   
5756    WBD         LinearSVR     0.996990    0.948905    0.099974   0.259076   
5757    WBD            RbfSVR     0.862325  -10.735785   22.962620   4.264687   
5758    WBD     PolynomialSVR     0.944130  -83.035867  164.427326  11.654887   
5759    WBD           XGBoost     0.999994   -0.620959    3.171622   1.457567   

           RMSE        MAPE       sMAPE         R2  ...  WF_sMAPE_1 ay  \
5748   1.709073   17.266550   15.176096  -0.492836  ...       4.032744   
5749   1.629196   16.490550   14.570633  -0.356555  ...       2.786070   
5750   2.088564   21.770129   18.766475  -1.229391  ...       7.799029   
5751   3.731189   41.546236   33.127079  -6.115168  ...      20.442567   
5752   2.684679   28.552506   24.351477  -2.683624  ...      24.358367   
5753   0.306897    2.842876    2.864281   0.951863  ...       2.526677   
5754   1.777654   14.701108   13.801378  -0.615047  ...      18.906515   
5755   0.307986    2.852637    2.874027   0.951521  ...       2.548230   
5756   0.316186    2.959497    2.993807   0.948905  ...       2.645440   
5757   4.791933   49.759305   37.971477 -10.735785  ...      37.925586   
5758  12.822922  137.948152  162.773529 -83.035867  ...     200.000000   
5759   1.780905   18.125601   15.864008  -0.620959  ...       2.915654   

      WF_RMSE_3 ay  WF_MAPE_3 ay  WF_sMAPE_3 ay  WF_RMSE_6 ay  WF_MAPE_6 ay  \
5748      0.876060      6.330661       5.871092      1.915468     19.619834   
5749      0.690829      5.122582       4.847782      1.747812     17.804046   
5750      1.173257      9.650734       8.867193      2.282208     24.277480   
5751      2.546523     24.717212      21.550735      3.826769     43.351239   
5752      3.317932     32.580005      27.753958      3.360453     37.631951   
5753      0.345290      2.787753       2.739421      0.333168      3.162051   
5754      3.106508     28.831808      24.890051      2.334768     19.840884   
5755      0.347840      2.810752       2.761237      0.334386      3.173019   
5756      0.356353      2.911525       2.858950      0.339471      3.230282   
5757      6.491809     62.096407      46.757317      5.981616     65.902741   
5758     14.866317    147.502668     200.000000     15.747710    181.274739   
5759      0.819951      5.843088       5.440060      1.905647     19.451439   

      WF_sMAPE_6 ay  WF_RMSE_1 yıl  WF_MAPE_1 yıl  WF_sMAPE_1 yıl  
5748      16.957263       1.863761      20.163046       17.665830  
5749      15.547654       1.778407      19.297974       16.997691  
5750      20.648496       2.279191      25.439559       21.853180  
5751      34.338510       4.024392      47.093931       37.201943  
5752      31.351646       2.877185      31.946326       27.048597  
5753       3.177600       0.314472       3.012464        3.042835  
5754      17.572064       1.826985      15.276620       14.354587  
5755       3.187939       0.315554       3.022188        3.052590  
5756       3.246766       0.328831       3.177508        3.222448  
5757      49.089891       5.216211      57.580500       43.569748  
5758     200.000000      13.994101     160.949506      190.113283  
5759      16.811923       1.940311      21.096939       18.396927  

[12 rows x 25 columns]